Comparing interharmonic modulations by plotting all possible changes. 

Only comparing Chan with weighted. Better graphs coming up

[Correlation Graph for n points](#correlation-plot)

In [1]:
import os
import sys
from pathlib import Path

sys.path.append(str(Path().cwd().parent))

sys.path.append(str(Path().cwd().parent.parent))



In [2]:
from psychoacoustic_tension_chan_module import interharmonic_module as ihm 
# interharmonic_module as ihm
import altair as alt
import pandas as pd
import numpy as np
from scipy import stats



# Ground truth definition

In [3]:

## Do intervals!

notes = ['G2','G#2','A2','A#2','B2','C3','C#3','D3','D#3','E3','F3','F#3','G3']

## generating intervals
intervals = []
for note in notes:
    intervals.append(['G2',note])

chord_labels_intervals = ['U', 'm2', 'M2', 'm3', 'M3', 'P4', 'TT', 'P5', 'm6', 'M6', 'm7', 'M7', '8v']

empirical_ranking_intervals = ['U','8v','P5','P4','M3','M6','m6','m3','TT','m7','M2','M7','m2']


## Triads to consider

triads=[
    # major
    ['C4', 'E4', 'G4'],
    ['C4', 'D#4','G#4'],
    ['C4', 'F4', 'A4'],
    #minor
    ['C4', 'D#4','G4'],
    ['C4', 'E4', 'A4'],
    ['C4', 'F4','G#4'],
    #Suspended
    ['C4', 'F4','G4'],
    ['C4', 'D4','G4'],
    ['C4', 'F4','A#4'],
    # Diminished,
    ['C4', 'D#4','F#4'],
    ['C4', 'D#4','A4'],
    ['C4', 'F#4','A4'],
    # augmented
    ['C4', 'E4','G#4'],
]
chord_labels_triads = ['CM', 'G#M1st', 'FM2nd', 'Cm', 'Am1st', 'Fm2nd', 'Csus4','Csus2', 'Fsus42nd', 'Cdim','Adim1st', 'F#dim2nd', 'CAug']
empirical_ranking_triads = ['CM', 'Cm', 'FM2nd', 'Fsus42nd', 'G#M1st','Csus2','Csus4', 'Fm2nd','Adim1st','Am1st', 'F#dim2nd','Cdim', 'CAug' ]
empirical_ranking_nums_triads = [1.667,2.407,2.741,2.852,2.889,3.111,3.148,3.481,3.519,3.593,3.667,3.889,5.259]


arrays_of_ranges = []
#define ranges for r_lower, r_upper
values_of_r_ranges = [0.0,0.125,0.25,0.5,1.5,2.5,3.5,4.5,5.5,6.5,7.5,8.5,9.5,10.5,11.5,12.5]

double_r_ranges = [(values_of_r_ranges[i], values_of_r_ranges[i+1]) for i in range(len(values_of_r_ranges)-1)]

arrays_of_ranges.append(double_r_ranges)

values_of_r_ranges = [0.25,0.5,1.5,2.5,3.5,4.5,5.5,6.5,7.5,8.5,9.5,10.5,11.5,12.5]
double_r_ranges = [(values_of_r_ranges[i], values_of_r_ranges[i+1]) for i in range(len(values_of_r_ranges)-1)]
arrays_of_ranges.append(double_r_ranges)

# Chan's method vanilla
r_ranges = [(0.95, 1.1), (1.5, 2.8)]
arrays_of_ranges.append(r_ranges)

r_range_methods = ['all_ranges', 'start_from_0.5', 'chan_vanilla']
file_path = Path.cwd().parent / 'data_csvs'/ 'all_interval_methods_with_results.csv'

# Key functions

## Now for interharmonic dataframe we have method, harmonics considered, normed values for interharmonic. Plan is to get reanking for each norm method and method and harmonics. 

In [4]:

from scipy.stats import pearsonr
normed_values_columns = ['normed_values_only_modulations','normed_values_weighted_modulations_only','normed_values_normed_weighted_modulations']
empirical_ranking_intervals = ['U','8v','P5','P4','M3','M6','m6','m3','TT','m7','M2','M7','m2']


def get_correlation_between_empirical_and_method(empirical_ranking, df_with_rankings, numbered_ranking=None,chord_label_column='chord_label', column_to_compare_with_emp='raw_t_score_summed_only_modulations'):
    ## first normalize empirical ranking

    empirical_ranking_numbered = range(0, len(empirical_ranking))

    if numbered_ranking is None:
        normalized_values = [x / max(empirical_ranking_numbered) for x in empirical_ranking_numbered]
    else:
        mininum = min(numbered_ranking) 
        maximum = max(numbered_ranking)
        normalized_values = [(x - mininum) / (maximum - mininum) for x in numbered_ranking]

    ## we are going to create a dictionary with the chord labels
    # with their respective scores. The plan is to see how correlated they are. 
    keys_for_dict = df_with_rankings[chord_label_column].tolist()
    
    ranked_df = {}
    for key in keys_for_dict:
        ranked_df[key] = df_with_rankings[df_with_rankings[chord_label_column] == key][column_to_compare_with_emp].values[0]
    
    ## now we are going to construct a list based on the empirical ranking 
    # using this dictionary

    for chord in empirical_ranking:
        if chord not in ranked_df.keys():
            print(f'Warning: chord {chord} not found in the dataframe keys')
            continue
    values_to_correlate = [ranked_df[chord] for chord in empirical_ranking]

    # get correlation
    corr, p_value = pearsonr(normalized_values, values_to_correlate)

    return corr, p_value, values_to_correlate


## Function to break into diff methods
Since there are multiple methods in each column, we can build an array of conditions

In [5]:


def break_into_different_rankings(biggest_df,empirical_ranking=[],numbered_ranking=None, method_columns=['method'],x_axis='harmonics_considered', normed_values_columns=normed_values_columns):
    ## Now for interharmonic dataframe we have method, harmonics considered, normed values for interharmonic. Plan is to get reanking for each norm method and method and harmonics. 
    
    new_df= pd.DataFrame()
    ## break_into_methods first

    methods_processed = 0

    ## we use a loop to get all different methods
    ## we get the method columns and drop duplicates

    methods = biggest_df[method_columns].drop_duplicates()

    ## then after getting methods, we use loop for building the conditions


    for index, row in methods.iterrows():
        conditions = None
        
        
        print('Processing new method combination:')
        for key, value in row.items():
            print(f'\t{key}: {value}')
            if conditions is None:
                conditions = (biggest_df[key] == value)
            else:
                conditions &= (biggest_df[key] == value)
        df_for_method = biggest_df[conditions]

        print('Cantidad' \
        ' de filas para este metodo:', len(df_for_method))
        print('----------------------------------')



        


    # for different_method in biggest_df[method_column].unique():
        # df_for_method = biggest_df[biggest_df[method_column] == different_method]
        # print(f'Now processing method {different_method}')
        # print(df_for_method)
        
        # print('----------------------------------')        

        ## after getting method, we need to get ranking order for each harmonics considered
        for harmonics in df_for_method[x_axis].unique():



            new_df_for_harmonics = df_for_method[df_for_method[x_axis] == harmonics]

            # print(f'Now processing harmonics {type(harmonics)}')
            # print(new_df_for_harmonics)
            # print('----------------------------------')


            # now we believe to have method and each harmonic. Now we need to rank for each
            # normed values column. We can do this by sorting values based on each column,
            # then assigning rank based on index position
            for normed_column in normed_values_columns:

                # print(f'Now processing normed column {normed_column}')
            
                # print(different_method, harmonics, normed_column)
                # print(type(different_method), type(harmonics), type(normed_column))
                

                ## Now for each normed column we are going to get correlation with empirical ranking
                # temp_df = pd.DataFrame()
                # temp_df['method'] = different_method
                # temp_df['harmonics_considered'] = harmonics
                # temp_df['normed_column'] = normed_column

                corr, p_value, values_to_correlate = get_correlation_between_empirical_and_method(empirical_ranking, df_with_rankings=new_df_for_harmonics, numbered_ranking=numbered_ranking, chord_label_column='chord_label', column_to_compare_with_emp=normed_column)

                # temp_df['correlation'] = corr
                # temp_df['p_value'] = p_value
                # temp_df['final_ranking_correlate'] = [values_to_correlate]

                temp_df = pd.DataFrame()

                # we need to take for method columns and put them in the temp df

                for key, value in row.items():
                    temp_df[key] = [value]
                
                temp_df['normed_column'] = [normed_column]
                temp_df['harmonics_considered'] = [harmonics]
                temp_df['correlation'] = [corr]
                temp_df['p_value'] = [p_value]
                temp_df['final_ranking_correlate'] = [values_to_correlate]

                # temp_df = pd.DataFrame({
                #     'method': [different_method + ' ' + normed_column],
                #     'harmonics_considered': [harmonics],
                #     'normed_column': [normed_column],
                #     'correlation': [corr],
                #     'p_value': [p_value],
                #     'final_ranking_correlate': [values_to_correlate]
                # })
                print(temp_df.to_string(index=False))
                

                methods_processed += 1

                new_df = pd.concat([new_df, temp_df], ignore_index=True)
    print(f'Total methods processed: {methods_processed}'  )
    return new_df



# IHM intervals

In [6]:

normed_values_columns = ['normed_values_only_modulations','normed_values_weighted_modulations_only','normed_values_normed_weighted_modulations']

biggest_df = ihm.pipeline_for_interharmonic_normalized_tension_scores(
    note_combinations_array=intervals,
    chord_labels_array=chord_labels_intervals,
    r_ranges=arrays_of_ranges,
    r_range_names=r_range_methods,
    file_path=file_path)

Now processing intervals
Now processing 2 harmonics
Now processing [(0.0, 0.125), (0.125, 0.25), (0.25, 0.5), (0.5, 1.5), (1.5, 2.5), (2.5, 3.5), (3.5, 4.5), (4.5, 5.5), (5.5, 6.5), (6.5, 7.5), (7.5, 8.5), (8.5, 9.5), (9.5, 10.5), (10.5, 11.5), (11.5, 12.5)] with ranges all_ranges


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries befo

Now processing [(0.25, 0.5), (0.5, 1.5), (1.5, 2.5), (2.5, 3.5), (3.5, 4.5), (4.5, 5.5), (5.5, 6.5), (6.5, 7.5), (7.5, 8.5), (8.5, 9.5), (9.5, 10.5), (10.5, 11.5), (11.5, 12.5)] with ranges start_from_0.5


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries befo

Now processing [(0.95, 1.1), (1.5, 2.8)] with ranges chan_vanilla
Now processing 3 harmonics
Now processing [(0.0, 0.125), (0.125, 0.25), (0.25, 0.5), (0.5, 1.5), (1.5, 2.5), (2.5, 3.5), (3.5, 4.5), (4.5, 5.5), (5.5, 6.5), (6.5, 7.5), (7.5, 8.5), (8.5, 9.5), (9.5, 10.5), (10.5, 11.5), (11.5, 12.5)] with ranges all_ranges


KeyboardInterrupt: 

CSV has 9 methods * 31 harmonics * 13 intervals = 3627 rows

In [70]:
biggest_df = pd.read_csv(file_path)

In [72]:
biggest_df[biggest_df['r_names_used']=='chan_vanilla']

note_combination chord_label raw_values_per_combination  \
104             G2,G2           U                   [[0, 0]]   
105             G2,B2          M3                   [[0, 0]]   
106             G2,C3          P4                   [[0, 0]]   
107            G2,C#3          TT                   [[0, 0]]   
108             G2,D3          P5                   [[0, 0]]   
...               ...         ...                        ...   
3622            G2,G2           U                  [[8, 80]]   
3623            G2,B2          M3                 [[13, 76]]   
3624            G2,A2          M2                  [[5, 85]]   
3625           G2,A#2          m3                  [[6, 92]]   
3626           G2,G#2          m2                 [[36, 81]]   

     weighted_modulations_per_region_in_note_combinations  \
104                                                 NaN     
105                                                 NaN     
106                                                 NaN     
107                                                 NaN     
108                                                 NaN     
...                                                 ...     
3622                                                NaN     
3623                                                NaN     
3624                                                NaN     
3625                                                NaN     
3626                                                NaN     

     weighted_sum_per_region_normalized_tension_value  \
104                                               NaN   
105                                               NaN   
106                                               NaN   
107                                               NaN   
108                                               NaN   
...                                               ...   
3622                                              NaN   
3623                                              NaN   
3624                                              NaN   
3625                                              NaN   
3626                                              NaN   

      raw_t_score_summed_only_modulations  \
104                                   0.0   
105                                   0.0   
106                                   0.0   
107                                   0.0   
108                                   0.0   
...                                   ...   
3622                                 88.0   
3623                                 89.0   
3624                                 90.0   
3625                                 98.0   
3626                                117.0   

      raw_t_score_summed_using_weighted_normalized_value  \
104                                                 NaN    
105                                                 NaN    
106                                                 NaN    
107                                                 NaN    
108                                                 NaN    
...                                                 ...    
3622                                                NaN    
3623                                                NaN    
3624                                                NaN    
3625                                                NaN    
3626                                                NaN    

      raw_t_score_summed_using_weighted_modulations_no_norm  \
104                                                 NaN       
105                                                 NaN       
106                                                 NaN       
107                                                 NaN       
108                                                 NaN       
...                                                 ...       
3622                                                NaN       
3623                                                

In [73]:
biggest_df[biggest_df['r_names_used']=='chan_vanilla']

note_combination chord_label raw_values_per_combination  \
104             G2,G2           U                   [[0, 0]]   
105             G2,B2          M3                   [[0, 0]]   
106             G2,C3          P4                   [[0, 0]]   
107            G2,C#3          TT                   [[0, 0]]   
108             G2,D3          P5                   [[0, 0]]   
...               ...         ...                        ...   
3622            G2,G2           U                  [[8, 80]]   
3623            G2,B2          M3                 [[13, 76]]   
3624            G2,A2          M2                  [[5, 85]]   
3625           G2,A#2          m3                  [[6, 92]]   
3626           G2,G#2          m2                 [[36, 81]]   

     weighted_modulations_per_region_in_note_combinations  \
104                                                 NaN     
105                                                 NaN     
106                                                 NaN     
107                                                 NaN     
108                                                 NaN     
...                                                 ...     
3622                                                NaN     
3623                                                NaN     
3624                                                NaN     
3625                                                NaN     
3626                                                NaN     

     weighted_sum_per_region_normalized_tension_value  \
104                                               NaN   
105                                               NaN   
106                                               NaN   
107                                               NaN   
108                                               NaN   
...                                               ...   
3622                                              NaN   
3623                                              NaN   
3624                                              NaN   
3625                                              NaN   
3626                                              NaN   

      raw_t_score_summed_only_modulations  \
104                                   0.0   
105                                   0.0   
106                                   0.0   
107                                   0.0   
108                                   0.0   
...                                   ...   
3622                                 88.0   
3623                                 89.0   
3624                                 90.0   
3625                                 98.0   
3626                                117.0   

      raw_t_score_summed_using_weighted_normalized_value  \
104                                                 NaN    
105                                                 NaN    
106                                                 NaN    
107                                                 NaN    
108                                                 NaN    
...                                                 ...    
3622                                                NaN    
3623                                                NaN    
3624                                                NaN    
3625                                                NaN    
3626                                                NaN    

      raw_t_score_summed_using_weighted_modulations_no_norm  \
104                                                 NaN       
105                                                 NaN       
106                                                 NaN       
107                                                 NaN       
108                                                 NaN       
...                                                 ...       
3622                                                NaN       
3623                                                

## For paper, consider only Method B and Method C
((weigths_on_harmonics == False) & (weights_on_regions == False)) and Method C

In [ ]:
method_b =biggest_df[(biggest_df['weights_on_harmonics']==False) & (biggest_df['r_names_used']!='chan_vanilla')]
method_b[(method_b['harmonics_considered']==6) & (method_b['chord_label']=='U')]


note_combination chord_label  \
495            G2,G2           U   
518            G2,G2           U   
547            G2,G2           U   
560            G2,G2           U   

                          raw_values_per_combination  \
495  [[6, 0, 0, 0, 0, 4, 2, 0, 4, 2, 0, 6, 0, 2, 4]]   
518  [[6, 0, 0, 0, 0, 4, 2, 0, 4, 2, 0, 6, 0, 2, 4]]   
547        [[0, 0, 0, 4, 2, 0, 4, 2, 0, 6, 0, 2, 4]]   
560        [[0, 0, 0, 4, 2, 0, 4, 2, 0, 6, 0, 2, 4]]   

    weighted_modulations_per_region_in_note_combinations  \
495  [[0, 0.0, 0.0, 0, 0, 2.8, 0, 0, 0, 0, 0.0, 0, ...     
518                                                NaN     
547    [[0.0, 0, 0, 2.8, 0, 0, 0, 0, 0.0, 0, 0, 0, 0]]     
560                                                NaN     

    weighted_sum_per_region_normalized_tension_value  \
495                            [0.09333333333333332]   
518                                              NaN   
547                            [0.11666666666666665]   
560                                              NaN   

     raw_t_score_summed_only_modulations  \
495                                 30.0   
518                                 30.0   
547                                 24.0   
560                                 24.0   

     raw_t_score_summed_using_weighted_normalized_value  \
495                                           0.093333    
518                                                NaN    
547                                           0.116667    
560                                                NaN    

     raw_t_score_summed_using_weighted_modulations_no_norm  \
495                                                2.8       
518                                                NaN       
547                                                2.8       
560                                                NaN       

     normed_values_only_modulations  \
495                        1.000000   
518                        1.000000   
547                        0.142857   
560                        0.142857   

     normed_values_normed_weighted_modulations  \
495                                   0.073747   
518                                        NaN   
547                                   0.105593   
560                                        NaN   

     normed_values_weighted_modulations_only                 method  \
495                                 0.092715  Experimental_methods    
518                                      NaN  Experimental_methods    
547                                 0.092715  Experimental_methods    
560                                      NaN  Experimental_methods    

                                         r_ranges_used    r_names_used  \
495  [[0.0, 0.125], [0.125, 0.25], [0.25, 0.5], [0....      all_ranges   
518  [[0.0, 0.125], [0.125, 0.25], [0.25, 0.5], [0....      all_ranges   
547  [[0.25, 0.5], [0.5, 1.5], [1.5, 2.5], [2.5, 3....  start_from_0.5   
560  [[0.25, 0.5], [0.5, 1.5], [1.5, 2.5], [2.5, 3....  start_from_0.5   

     distributive  harmonics_considered  weights_on_harmonics  \
495          True                     6                 False   
518          True                     6                 False   
547          True                     6                 False   
560          True                     6                 False   

     weights_on_regions                                weights_for_regions  
495                True  {'red_region': 1, 'orange_region': 0.7, 'yello...  
518               False                                                NaN  
547                True  {'red_region': 1, 'orange_region': 0.7, 'yello...  
560               False                                                NaN

In [253]:
method_b[(method_b['harmonics_considered']==6) & (method_b['chord_label']=='m2')]

note_combination chord_label  \
505           G2,G#2          m2   
519           G2,G#2          m2   
557           G2,G#2          m2   
571           G2,G#2          m2   

                          raw_values_per_combination  \
505  [[0, 0, 0, 6, 1, 1, 3, 3, 3, 0, 4, 3, 1, 1, 4]]   
519  [[0, 0, 0, 6, 1, 1, 3, 3, 3, 0, 4, 3, 1, 1, 4]]   
557        [[0, 6, 1, 1, 3, 3, 3, 0, 4, 3, 1, 1, 4]]   
571        [[0, 6, 1, 1, 3, 3, 3, 0, 4, 3, 1, 1, 4]]   

    weighted_modulations_per_region_in_note_combinations  \
505  [[0, 0.0, 0.0, 6, 1, 0.7, 0, 3, 0, 0, 2.8, 0, ...     
519                                                NaN     
557    [[0.0, 6, 1, 0.7, 0, 3, 0, 0, 2.8, 0, 0, 0, 0]]     
571                                                NaN     

    weighted_sum_per_region_normalized_tension_value  \
505                                           [0.45]   
519                                              NaN   
557                                           [0.45]   
571                                              NaN   

     raw_t_score_summed_only_modulations  \
505                                 30.0   
519                                 30.0   
557                                 30.0   
571                                 30.0   

     raw_t_score_summed_using_weighted_normalized_value  \
505                                               0.45    
519                                                NaN    
557                                               0.45    
571                                                NaN    

     raw_t_score_summed_using_weighted_modulations_no_norm  \
505                                               13.5       
519                                                NaN       
557                                               13.5       
571                                                NaN       

     normed_values_only_modulations  \
505                             1.0   
519                             1.0   
557                             1.0   
571                             1.0   

     normed_values_normed_weighted_modulations  \
505                                   0.739867   
519                                        NaN   
557                                   0.736409   
571                                        NaN   

     normed_values_weighted_modulations_only                 method  \
505                                 0.801325  Experimental_methods    
519                                      NaN  Experimental_methods    
557                                 0.801325  Experimental_methods    
571                                      NaN  Experimental_methods    

                                         r_ranges_used    r_names_used  \
505  [[0.0, 0.125], [0.125, 0.25], [0.25, 0.5], [0....      all_ranges   
519  [[0.0, 0.125], [0.125, 0.25], [0.25, 0.5], [0....      all_ranges   
557  [[0.25, 0.5], [0.5, 1.5], [1.5, 2.5], [2.5, 3....  start_from_0.5   
571  [[0.25, 0.5], [0.5, 1.5], [1.5, 2.5], [2.5, 3....  start_from_0.5   

     distributive  harmonics_considered  weights_on_harmonics  \
505          True                     6                 False   
519          True                     6                 False   
557          True                     6                 False   
571          True                     6                 False   

     weights_on_regions                                weights_for_regions  
505                True  {'red_region': 1, 'orange_region': 0.7, 'yello...  
519               False                                                NaN  
557                True  {'red_region': 1, 'orange_region': 0.7, 'yello...  
571               False                                                NaN

In [47]:
row_of_dif_methods = biggest_df[['method','r_names_used','distributive','weights_on_harmonics','weights_on_regions']].drop_duplicates()

row_of_dif_methods

method    r_names_used  distributive  \
0    Experimental_methods       all_ranges          True   
13   Experimental_methods       all_ranges          True   
26   Experimental_methods       all_ranges          True   
39   Experimental_methods       all_ranges          True   
52   Experimental_methods   start_from_0.5          True   
65   Experimental_methods   start_from_0.5          True   
78   Experimental_methods   start_from_0.5          True   
91   Experimental_methods   start_from_0.5          True   
104  Chan's method Vanilla    chan_vanilla          True   

     weights_on_harmonics  weights_on_regions  
0                    True                True  
13                   True               False  
26                  False                True  
39                  False               False  
52                   True                True  
65                   True               False  
78                  False                True  
91                  False               False  
104                 False               False

In [65]:

count_methods_with_null = 0
for index, row in row_of_dif_methods.iterrows():

    conditions = None
    for key, value in row.items():
        print(f'{key}: {value}')
        if conditions is None:
            conditions = (biggest_df[key] == value)
        else:
            conditions &= (biggest_df[key] == value)
    print('Combinations with NaN values for this method:')
    print(biggest_df[conditions].notna().sum())


    
biggest_df[conditions]

method: Experimental_methods 
r_names_used: all_ranges
distributive: True
weights_on_harmonics: True
weights_on_regions: True
Combinations with NaN values for this method:
note_combination                                         403
chord_label                                              403
raw_values_per_combination                               403
weighted_modulations_per_region_in_note_combinations     403
weighted_sum_per_region_normalized_tension_value         403
raw_t_score_summed_only_modulations                      403
raw_t_score_summed_using_weighted_normalized_value       403
raw_t_score_summed_using_weighted_modulations_no_norm    403
normed_values_only_modulations                           403
normed_values_normed_weighted_modulations                403
normed_values_weighted_modulations_only                  403
method                                                   403
r_ranges_used                                            403
r_names_used                       

note_combination chord_label raw_values_per_combination  \
104             G2,G2           U                   [[0, 0]]   
105             G2,B2          M3                   [[0, 0]]   
106             G2,C3          P4                   [[0, 0]]   
107            G2,C#3          TT                   [[0, 0]]   
108             G2,D3          P5                   [[0, 0]]   
...               ...         ...                        ...   
3622            G2,G2           U                  [[8, 80]]   
3623            G2,B2          M3                 [[13, 76]]   
3624            G2,A2          M2                  [[5, 85]]   
3625           G2,A#2          m3                  [[6, 92]]   
3626           G2,G#2          m2                 [[36, 81]]   

     weighted_modulations_per_region_in_note_combinations  \
104                                                None     
105                                                None     
106                                                None     
107                                                None     
108                                                None     
...                                                 ...     
3622                                               None     
3623                                               None     
3624                                               None     
3625                                               None     
3626                                               None     

     weighted_sum_per_region_normalized_tension_value  \
104                                              None   
105                                              None   
106                                              None   
107                                              None   
108                                              None   
...                                               ...   
3622                                             None   
3623                                             None   
3624                                             None   
3625                                             None   
3626                                             None   

      raw_t_score_summed_only_modulations  \
104                                   0.0   
105                                   0.0   
106                                   0.0   
107                                   0.0   
108                                   0.0   
...                                   ...   
3622                                 88.0   
3623                                 89.0   
3624                                 90.0   
3625                                 98.0   
3626                                117.0   

      raw_t_score_summed_using_weighted_normalized_value  \
104                                                 NaN    
105                                                 NaN    
106                                                 NaN    
107                                                 NaN    
108                                                 NaN    
...                                                 ...    
3622                                                NaN    
3623                                                NaN    
3624                                                NaN    
3625                                                NaN    
3626                                                NaN    

      raw_t_score_summed_using_weighted_modulations_no_norm  \
104                                                 NaN       
105                                                 NaN       
106                                                 NaN       
107                                                 NaN       
108                                                 NaN       
...                                                 ...       
3622                                                NaN       
3623                                                

In [52]:

method_columns = ['method','r_names_used','distributive','weights_on_harmonics','weights_on_regions']

new_df = break_into_different_rankings(biggest_df,empirical_ranking=empirical_ranking_intervals, method_columns=method_columns,x_axis='harmonics_considered', normed_values_columns=normed_values_columns)


Processing new method combination:
	method: Experimental_methods 
	r_names_used: all_ranges
	distributive: True
	weights_on_harmonics: True
	weights_on_regions: True
Cantidad de filas para este metodo: 403
----------------------------------
               method r_names_used  distributive  weights_on_harmonics  weights_on_regions                  normed_column  harmonics_considered  correlation  p_value                                           final_ranking_correlate
Experimental_methods    all_ranges          True                  True                True normed_values_only_modulations                     2    -0.089087 0.772261 [1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 0.0, 1.0]
               method r_names_used  distributive  weights_on_harmonics  weights_on_regions                           normed_column  harmonics_considered  correlation  p_value                                                                                               final_ranking_correlate
Ex

CSV with correlation has 9 methods * 3 normalizations * 31 harmonics = 837

In [67]:
new_df

method  r_names_used  distributive  weights_on_harmonics  \
0    Experimental_methods     all_ranges          True                  True   
1    Experimental_methods     all_ranges          True                  True   
2    Experimental_methods     all_ranges          True                  True   
3    Experimental_methods     all_ranges          True                  True   
4    Experimental_methods     all_ranges          True                  True   
..                     ...           ...           ...                   ...   
832  Chan's method Vanilla  chan_vanilla          True                 False   
833  Chan's method Vanilla  chan_vanilla          True                 False   
834  Chan's method Vanilla  chan_vanilla          True                 False   
835  Chan's method Vanilla  chan_vanilla          True                 False   
836  Chan's method Vanilla  chan_vanilla          True                 False   

     weights_on_regions                              normed_column  \
0                  True             normed_values_only_modulations   
1                  True    normed_values_weighted_modulations_only   
2                  True  normed_values_normed_weighted_modulations   
3                  True             normed_values_only_modulations   
4                  True    normed_values_weighted_modulations_only   
..                  ...                                        ...   
832               False    normed_values_weighted_modulations_only   
833               False  normed_values_normed_weighted_modulations   
834               False             normed_values_only_modulations   
835               False    normed_values_weighted_modulations_only   
836               False  normed_values_normed_weighted_modulations   

     harmonics_considered  correlation   p_value  \
0                       2    -0.089087  0.772261   
1                       2     0.885942  0.000056   
2                       2     0.887170  0.000052   
3                       3    -0.062137  0.840185   
4                       3     0.914592  0.000012   
..                    ...          ...       ...   
832                    31          NaN       NaN   
833                    31          NaN       NaN   
834                    32     0.412435  0.161363   
835                    32          NaN       NaN   
836                    32          NaN       NaN   

                               final_ranking_correlate  
0    [1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, ...  
1    [0.0, 0.0, 0.0, 0.0, 0.0, 0.17499999999999996,...  
2    [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314,...  
3    [1.0, 0.0, 0.5, 0.5000000000000003, 0.50000000...  
4    [0.0, 0.0, 0.0, 0.12500000000000003, 0.21875, ...  
..                                                 ...  
832  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...  
833  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...  
834  [0.5606060606060606, 0.0, 0.19696969696969696,...  
835  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...  
836  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...  

[837 rows x 10 columns]

CSV when na dropped we have 
(9 methods * 3 normalizations * 31 harmonics) - (5 methods * 2 normalized methods they do not have * 31 harmonics )= 527

In [ ]:


# new_df.method.unique()
df_to_work_with = new_df.dropna()

df_to_work_with.to_csv('../data_csvs/overall_interharmonic_normalized_tension_scores_correlation_with_empirical_intervals.csv', index=False)

In [ ]:
df_to_work_with

method  r_names_used  distributive  weights_on_harmonics  \
0    Experimental_methods     all_ranges          True                  True   
1    Experimental_methods     all_ranges          True                  True   
2    Experimental_methods     all_ranges          True                  True   
3    Experimental_methods     all_ranges          True                  True   
4    Experimental_methods     all_ranges          True                  True   
..                     ...           ...           ...                   ...   
822  Chan's method Vanilla  chan_vanilla          True                 False   
825  Chan's method Vanilla  chan_vanilla          True                 False   
828  Chan's method Vanilla  chan_vanilla          True                 False   
831  Chan's method Vanilla  chan_vanilla          True                 False   
834  Chan's method Vanilla  chan_vanilla          True                 False   

     weights_on_regions                              normed_column  \
0                  True             normed_values_only_modulations   
1                  True    normed_values_weighted_modulations_only   
2                  True  normed_values_normed_weighted_modulations   
3                  True             normed_values_only_modulations   
4                  True    normed_values_weighted_modulations_only   
..                  ...                                        ...   
822               False             normed_values_only_modulations   
825               False             normed_values_only_modulations   
828               False             normed_values_only_modulations   
831               False             normed_values_only_modulations   
834               False             normed_values_only_modulations   

     harmonics_considered  correlation   p_value  \
0                       2    -0.089087  0.772261   
1                       2     0.885942  0.000056   
2                       2     0.887170  0.000052   
3                       3    -0.062137  0.840185   
4                       3     0.914592  0.000012   
..                    ...          ...       ...   
822                    28     0.486403  0.091901   
825                    29     0.485307  0.092744   
828                    30     0.480084  0.096840   
831                    31     0.446446  0.126195   
834                    32     0.412435  0.161363   

                               final_ranking_correlate  
0    [1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, ...  
1    [0.0, 0.0, 0.0, 0.0, 0.0, 0.17499999999999996,...  
2    [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314,...  
3    [1.0, 0.0, 0.5, 0.5000000000000003, 0.50000000...  
4    [0.0, 0.0, 0.0, 0.12500000000000003, 0.21875, ...  
..                                                 ...  
822  [0.5172413793103449, 0.0, 0.22413793103448276,...  
825  [0.5, 0.0, 0.20967741935483872, 0.338709677419...  
828  [0.49230769230769234, 0.0, 0.2153846153846154,...  
831  [0.5151515151515151, 0.0, 0.21212121212121213,...  
834  [0.5606060606060606, 0.0, 0.19696969696969696,...  

[527 rows x 10 columns]

## Read CSV make graphs

In [6]:
df_to_work_with = pd.read_csv('../data_csvs/overall_interharmonic_normalized_tension_scores_correlation_with_empirical_intervals.csv')

In [ ]:
df_to_work_with

method  r_names_used  distributive  weights_on_harmonics  \
0    Experimental_methods     all_ranges          True                  True   
1    Experimental_methods     all_ranges          True                  True   
2    Experimental_methods     all_ranges          True                  True   
3    Experimental_methods     all_ranges          True                  True   
4    Experimental_methods     all_ranges          True                  True   
..                     ...           ...           ...                   ...   
522  Chan's method Vanilla  chan_vanilla          True                 False   
523  Chan's method Vanilla  chan_vanilla          True                 False   
524  Chan's method Vanilla  chan_vanilla          True                 False   
525  Chan's method Vanilla  chan_vanilla          True                 False   
526  Chan's method Vanilla  chan_vanilla          True                 False   

     weights_on_regions                              normed_column  \
0                  True             normed_values_only_modulations   
1                  True    normed_values_weighted_modulations_only   
2                  True  normed_values_normed_weighted_modulations   
3                  True             normed_values_only_modulations   
4                  True    normed_values_weighted_modulations_only   
..                  ...                                        ...   
522               False             normed_values_only_modulations   
523               False             normed_values_only_modulations   
524               False             normed_values_only_modulations   
525               False             normed_values_only_modulations   
526               False             normed_values_only_modulations   

     harmonics_considered  correlation   p_value  \
0                       2    -0.089087  0.772261   
1                       2     0.885942  0.000056   
2                       2     0.887170  0.000052   
3                       3    -0.062137  0.840185   
4                       3     0.914592  0.000012   
..                    ...          ...       ...   
522                    28     0.486403  0.091901   
523                    29     0.485307  0.092744   
524                    30     0.480084  0.096840   
525                    31     0.446446  0.126195   
526                    32     0.412435  0.161363   

                               final_ranking_correlate  
0    [1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, ...  
1    [0.0, 0.0, 0.0, 0.0, 0.0, 0.17499999999999996,...  
2    [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314,...  
3    [1.0, 0.0, 0.5, 0.5000000000000003, 0.50000000...  
4    [0.0, 0.0, 0.0, 0.12500000000000003, 0.21875, ...  
..                                                 ...  
522  [0.5172413793103449, 0.0, 0.22413793103448276,...  
523  [0.5, 0.0, 0.20967741935483872, 0.338709677419...  
524  [0.49230769230769234, 0.0, 0.2153846153846154,...  
525  [0.5151515151515151, 0.0, 0.21212121212121213,...  
526  [0.5606060606060606, 0.0, 0.19696969696969696,...  

[527 rows x 10 columns]

## cleaning method names, divide by cases based on thesis


In [ ]:

df_to_work_with[df_to_work_with['weights_on_harmonics']==False]['method']

In [20]:

def name_conditions(biggest_df):
    # conditions = {
    #     ## method A is vanilla method
    #     'Method A': biggest_df['weights_on_harmonics']==False & biggest_df['weights_on_regions']==False & biggest_df['r_names_used'] == 'chan_vanilla',
    #     ## Method B is considering different ranges
    #     'Method B': biggest_df['weights_on_harmonics']==False & biggest_df['weights_on_regions']==False & biggest_df['r_names_used'] != 'chan_vanilla',
    #     ## Method C is considering different weights on regions
    #     'Method C': biggest_df['weights_on_harmonics']==False & biggest_df['weights_on_regions'],
    #     ## Method D is considering different weights on harmonics
    #     'Method D': biggest_df['weights_on_harmonics'] & biggest_df['weights_on_regions']==False,
    #     ## Method E is considering different weights on harmonics and regions
    #     'Method E': biggest_df['weights_on_harmonics'] & biggest_df['weights_on_regions'],
    # }
    biggest_df['cleaned_method_name'] = None


    biggest_df.loc[((biggest_df['weights_on_harmonics']==False) & (biggest_df['weights_on_regions']==False) & (biggest_df['r_names_used'] == 'chan_vanilla')),'cleaned_method_name'] = 'Method A'
    biggest_df.loc[((biggest_df['weights_on_harmonics']==False) & (biggest_df['weights_on_regions']==False) & (biggest_df['r_names_used'] != 'chan_vanilla')),'cleaned_method_name'] = 'Method B'
    biggest_df.loc[((biggest_df['weights_on_harmonics']==False) & (biggest_df['weights_on_regions']==True)),'cleaned_method_name'] = 'Method C'
    biggest_df.loc[((biggest_df['weights_on_harmonics']==True) & (biggest_df['weights_on_regions']==False)),'cleaned_method_name'] = 'Method D'
    biggest_df.loc[((biggest_df['weights_on_harmonics']==True) & (biggest_df['weights_on_regions']==True)),'cleaned_method_name'] = 'Method E'
    # for name, condition in conditions.items():
    #     biggest_df[condition]['cleaned_method_name'] = name
    # return biggest_df


In [ ]:

name_conditions(df_to_work_with)
df_to_work_with

In [ ]:
df_to_work_with.to_csv('../data_csvs/overall_interharmonic_normalized_tension_scores_correlation_with_empirical_intervals.csv', index=False)

## Reading last csv.

In [ ]:
df_to_work_with = pd.read_csv('../data_csvs/overall_interharmonic_normalized_tension_scores_correlation_with_empirical_intervals.csv')
df_to_work_with

method  r_names_used  distributive  weights_on_harmonics  \
0    Experimental_methods     all_ranges          True                  True   
1    Experimental_methods     all_ranges          True                  True   
2    Experimental_methods     all_ranges          True                  True   
3    Experimental_methods     all_ranges          True                  True   
4    Experimental_methods     all_ranges          True                  True   
..                     ...           ...           ...                   ...   
522  Chan's method Vanilla  chan_vanilla          True                 False   
523  Chan's method Vanilla  chan_vanilla          True                 False   
524  Chan's method Vanilla  chan_vanilla          True                 False   
525  Chan's method Vanilla  chan_vanilla          True                 False   
526  Chan's method Vanilla  chan_vanilla          True                 False   

     weights_on_regions                              normed_column  \
0                  True             normed_values_only_modulations   
1                  True    normed_values_weighted_modulations_only   
2                  True  normed_values_normed_weighted_modulations   
3                  True             normed_values_only_modulations   
4                  True    normed_values_weighted_modulations_only   
..                  ...                                        ...   
522               False             normed_values_only_modulations   
523               False             normed_values_only_modulations   
524               False             normed_values_only_modulations   
525               False             normed_values_only_modulations   
526               False             normed_values_only_modulations   

     harmonics_considered  correlation   p_value  \
0                       2    -0.089087  0.772261   
1                       2     0.885942  0.000056   
2                       2     0.887170  0.000052   
3                       3    -0.062137  0.840185   
4                       3     0.914592  0.000012   
..                    ...          ...       ...   
522                    28     0.486403  0.091901   
523                    29     0.485307  0.092744   
524                    30     0.480084  0.096840   
525                    31     0.446446  0.126195   
526                    32     0.412435  0.161363   

                               final_ranking_correlate cleaned_method_name  
0    [1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, ...            Method E  
1    [0.0, 0.0, 0.0, 0.0, 0.0, 0.17499999999999996,...            Method E  
2    [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314,...            Method E  
3    [1.0, 0.0, 0.5, 0.5000000000000003, 0.50000000...            Method E  
4    [0.0, 0.0, 0.0, 0.12500000000000003, 0.21875, ...            Method E  
..                                                 ...                 ...  
522  [0.5172413793103449, 0.0, 0.22413793103448276,...            Method A  
523  [0.5, 0.0, 0.20967741935483872, 0.338709677419...            Method A  
524  [0.49230769230769234, 0.0, 0.2153846153846154,...            Method A  
525  [0.5151515151515151, 0.0, 0.21212121212121213,...            Method A  
526  [0.5606060606060606, 0.0, 0.19696969696969696,...            Method A  

[527 rows x 11 columns]

## cleaning method names with correct normed_column


In [ ]:

df_to_work_with[df_to_work_with['cleaned_method_name']=='Method A']

In [ ]:
df_to_work_with[df_to_work_with['cleaned_method_name']=='Method B']

NameError: name 'df_to_work_with' is not defined

In [26]:
df_to_work_with[df_to_work_with['cleaned_method_name']=='Method C']

NameError: name 'df_to_work_with' is not defined

In [ ]:
df_to_work_with.drop(df_to_work_with[(df_to_work_with['cleaned_method_name']=='Method C') & (df_to_work_with['normed_column']!='normed_values_normed_weighted_modulations')].index, inplace=True)
df_to_work_with[df_to_work_with['cleaned_method_name']=='Method C']

method    r_names_used  distributive  \
126  Experimental_methods       all_ranges          True   
129  Experimental_methods       all_ranges          True   
132  Experimental_methods       all_ranges          True   
135  Experimental_methods       all_ranges          True   
138  Experimental_methods       all_ranges          True   
..                     ...             ...           ...   
452  Experimental_methods   start_from_0.5          True   
455  Experimental_methods   start_from_0.5          True   
458  Experimental_methods   start_from_0.5          True   
461  Experimental_methods   start_from_0.5          True   
464  Experimental_methods   start_from_0.5          True   

     weights_on_harmonics  weights_on_regions  \
126                 False                True   
129                 False                True   
132                 False                True   
135                 False                True   
138                 False                True   
..                    ...                 ...   
452                 False                True   
455                 False                True   
458                 False                True   
461                 False                True   
464                 False                True   

                                 normed_column  harmonics_considered  \
126  normed_values_normed_weighted_modulations                     2   
129  normed_values_normed_weighted_modulations                     3   
132  normed_values_normed_weighted_modulations                     4   
135  normed_values_normed_weighted_modulations                     5   
138  normed_values_normed_weighted_modulations                     6   
..                                         ...                   ...   
452  normed_values_normed_weighted_modulations                    28   
455  normed_values_normed_weighted_modulations                    29   
458  normed_values_normed_weighted_modulations                    30   
461  normed_values_normed_weighted_modulations                    31   
464  normed_values_normed_weighted_modulations                    32   

     correlation   p_value                            final_ranking_correlate  \
126     0.887998  0.000050  [0.0, 0.0, 0.0, 0.0, 0.0, 0.2916666666666667, ...   
129     0.904415  0.000022  [0.0, 0.0, 0.0, 0.2, 0.27999999999999997, 0.54...   
132     0.925011  0.000006  [0.0, 0.0, 0.1149425287356322, 0.1954022988505...   
135     0.841085  0.000315  [0.0, 0.019379844961240317, 0.1802325581395349...   
138     0.839779  0.000328  [0.0737472207969899, 0.0, 0.21959979476654695,...   
..           ...       ...                                                ...   
452     0.225927  0.457971  [0.9254933910190899, 0.0, 0.38349173948460014,...   
455     0.224071  0.461772  [0.9252674957268413, 0.0, 0.3799305900078087, ...   
458     0.201183  0.509845  [0.9758493222618485, 0.0, 0.39688088260401794,...   
461     0.187948  0.538624  [0.9744604032959776, 0.0, 0.4234516378142172, ...   
464     0.179283  0.557833  [0.9854081265540123, 0.0, 0.4235969715185777, ...   

    cleaned_method_name  
126            Method C  
129            Method C  
132            Method C  
135            Method C  
138            Method C  
..                  ...  
452            Method C  
455            Method C  
458            Method C  
461            Method C  
464            Method C  

[62 rows x 11 columns]

In [ ]:
df_to_work_with[df_to_work_with['cleaned_method_name']=='Method D']

method    r_names_used  distributive  \
93   Experimental_methods       all_ranges          True   
94   Experimental_methods       all_ranges          True   
95   Experimental_methods       all_ranges          True   
96   Experimental_methods       all_ranges          True   
97   Experimental_methods       all_ranges          True   
..                     ...             ...           ...   
367  Experimental_methods   start_from_0.5          True   
368  Experimental_methods   start_from_0.5          True   
369  Experimental_methods   start_from_0.5          True   
370  Experimental_methods   start_from_0.5          True   
371  Experimental_methods   start_from_0.5          True   

     weights_on_harmonics  weights_on_regions                   normed_column  \
93                   True               False  normed_values_only_modulations   
94                   True               False  normed_values_only_modulations   
95                   True               False  normed_values_only_modulations   
96                   True               False  normed_values_only_modulations   
97                   True               False  normed_values_only_modulations   
..                    ...                 ...                             ...   
367                  True               False  normed_values_only_modulations   
368                  True               False  normed_values_only_modulations   
369                  True               False  normed_values_only_modulations   
370                  True               False  normed_values_only_modulations   
371                  True               False  normed_values_only_modulations   

     harmonics_considered  correlation   p_value  \
93                      2    -0.089087  0.772261   
94                      3    -0.062137  0.840185   
95                      4    -0.109172  0.722569   
96                      5    -0.015259  0.960541   
97                      6    -0.024264  0.937286   
..                    ...          ...       ...   
367                    28     0.176475  0.564118   
368                    29     0.170148  0.578387   
369                    30     0.166196  0.587372   
370                    31     0.160093  0.601355   
371                    32     0.154116  0.615173   

                               final_ranking_correlate cleaned_method_name  
93   [1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, ...            Method D  
94   [1.0, 0.0, 0.5, 0.5000000000000003, 0.50000000...            Method D  
95   [1.0, 0.0, 0.6666666666666667, 0.6666666666666...            Method D  
96   [1.0, 0.0, 0.5664739884393064, 0.5664739884393...            Method D  
97   [1.0, 0.0, 0.5070422535211264, 0.5070422535211...            Method D  
..                                                 ...                 ...  
367  [0.8032321982103053, 0.0, 0.4955111418583842, ...            Method D  
368  [0.815247982497089, 0.0, 0.49598717575755435, ...            Method D  
369  [0.8190877140603191, 0.0, 0.49504602196494, 0....            Method D  
370  [0.8292673977317409, 0.0, 0.4962632613956242, ...            Method D  
371  [0.8392975044057915, 0.0, 0.49824694650148643,...            Method D  

[62 rows x 11 columns]

In [ ]:
df_to_work_with[df_to_work_with['cleaned_method_name']=='Method E']

method    r_names_used  distributive  \
0    Experimental_methods       all_ranges          True   
1    Experimental_methods       all_ranges          True   
2    Experimental_methods       all_ranges          True   
3    Experimental_methods       all_ranges          True   
4    Experimental_methods       all_ranges          True   
..                     ...             ...           ...   
336  Experimental_methods   start_from_0.5          True   
337  Experimental_methods   start_from_0.5          True   
338  Experimental_methods   start_from_0.5          True   
339  Experimental_methods   start_from_0.5          True   
340  Experimental_methods   start_from_0.5          True   

     weights_on_harmonics  weights_on_regions  \
0                    True                True   
1                    True                True   
2                    True                True   
3                    True                True   
4                    True                True   
..                    ...                 ...   
336                  True                True   
337                  True                True   
338                  True                True   
339                  True                True   
340                  True                True   

                                 normed_column  harmonics_considered  \
0               normed_values_only_modulations                     2   
1      normed_values_weighted_modulations_only                     2   
2    normed_values_normed_weighted_modulations                     2   
3               normed_values_only_modulations                     3   
4      normed_values_weighted_modulations_only                     3   
..                                         ...                   ...   
336    normed_values_weighted_modulations_only                    31   
337  normed_values_normed_weighted_modulations                    31   
338             normed_values_only_modulations                    32   
339    normed_values_weighted_modulations_only                    32   
340  normed_values_normed_weighted_modulations                    32   

     correlation   p_value                            final_ranking_correlate  \
0      -0.089087  0.772261  [1.0, 0.0, 1.0, 1.0, 1.0, 0.0, 1.0, 1.0, 1.0, ...   
1       0.885942  0.000056  [0.0, 0.0, 0.0, 0.0, 0.0, 0.17499999999999996,...   
2       0.887170  0.000052  [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314,...   
3      -0.062137  0.840185  [1.0, 0.0, 0.5, 0.5000000000000003, 0.50000000...   
4       0.914592  0.000012  [0.0, 0.0, 0.0, 0.12500000000000003, 0.21875, ...   
..           ...       ...                                                ...   
336     0.551815  0.050567  [0.6304636263549722, 0.0, 0.30175346929660896,...   
337     0.768445  0.002149  [0.47724745353351805, 0.0, 0.17962847144225624...   
338     0.154116  0.615173  [0.8392975044057915, 0.0, 0.49824694650148643,...   
339     0.538032  0.057873  [0.6434483196669364, 0.0, 0.3054614913515351, ...   
340     0.761590  0.002487  [0.4940517685084168, 0.0, 0.1840972959293266, ...   

    cleaned_method_name  
0              Method E  
1              Method E  
2              Method E  
3              Method E  
4              Method E  
..                  ...  
336            Method E  
337            Method E  
338            Method E  
339            Method E  
340            Method E  

[186 rows x 11 columns]

In [ ]:
df_to_work_with.drop(df_to_work_with[(df_to_work_with['cleaned_method_name']=='Method E') & (df_to_work_with['normed_column']!='normed_values_normed_weighted_modulations')].index, inplace=True)   
df_to_work_with[df_to_work_with['cleaned_method_name']=='Method E']

method    r_names_used  distributive  \
2    Experimental_methods       all_ranges          True   
5    Experimental_methods       all_ranges          True   
8    Experimental_methods       all_ranges          True   
11   Experimental_methods       all_ranges          True   
14   Experimental_methods       all_ranges          True   
..                     ...             ...           ...   
328  Experimental_methods   start_from_0.5          True   
331  Experimental_methods   start_from_0.5          True   
334  Experimental_methods   start_from_0.5          True   
337  Experimental_methods   start_from_0.5          True   
340  Experimental_methods   start_from_0.5          True   

     weights_on_harmonics  weights_on_regions  \
2                    True                True   
5                    True                True   
8                    True                True   
11                   True                True   
14                   True                True   
..                    ...                 ...   
328                  True                True   
331                  True                True   
334                  True                True   
337                  True                True   
340                  True                True   

                                 normed_column  harmonics_considered  \
2    normed_values_normed_weighted_modulations                     2   
5    normed_values_normed_weighted_modulations                     3   
8    normed_values_normed_weighted_modulations                     4   
11   normed_values_normed_weighted_modulations                     5   
14   normed_values_normed_weighted_modulations                     6   
..                                         ...                   ...   
328  normed_values_normed_weighted_modulations                    28   
331  normed_values_normed_weighted_modulations                    29   
334  normed_values_normed_weighted_modulations                    30   
337  normed_values_normed_weighted_modulations                    31   
340  normed_values_normed_weighted_modulations                    32   

     correlation   p_value                            final_ranking_correlate  \
2       0.887170  0.000052  [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314,...   
5       0.903150  0.000023  [0.0, 0.0, 0.0, 0.125, 0.21875, 0.441964285714...   
8       0.916195  0.000011  [0.0, 0.0, 0.06849315068493153, 0.155251141552...   
11      0.877249  0.000082  [0.0, 0.01986123209400906, 0.11665631331368023...   
14      0.875810  0.000087  [0.02816911025807649, 0.0, 0.1413188191357587,...   
..           ...       ...                                                ...   
328     0.781499  0.001605  [0.43769227090262147, 0.0, 0.15972341793453823...   
331     0.781125  0.001618  [0.4442190314977679, 0.0, 0.16052218746492977,...   
334     0.771088  0.002028  [0.4780961599860561, 0.0, 0.1704374162429066, ...   
337     0.768445  0.002149  [0.47724745353351805, 0.0, 0.17962847144225624...   
340     0.761590  0.002487  [0.4940517685084168, 0.0, 0.1840972959293266, ...   

    cleaned_method_name  
2              Method E  
5              Method E  
8              Method E  
11             Method E  
14             Method E  
..                  ...  
328            Method E  
331            Method E  
334            Method E  
337            Method E  
340            Method E  

[62 rows x 11 columns]

## Saving clean intervals

In [ ]:
df_to_work_with.to_csv('../data_csvs/clean_ihm_intervals_normalized_tension_scores_correlation.csv', index=False)

# IHM triads

## Ground truth

In [6]:
## Triads to consider

triads=[
    # major
    ['C4', 'E4', 'G4'],
    ['C4', 'D#4','G#4'],
    ['C4', 'F4', 'A4'],
    #minor
    ['C4', 'D#4','G4'],
    ['C4', 'E4', 'A4'],
    ['C4', 'F4','G#4'],
    #Suspended
    ['C4', 'F4','G4'],
    ['C4', 'D4','G4'],
    ['C4', 'F4','A#4'],
    # Diminished,
    ['C4', 'D#4','F#4'],
    ['C4', 'D#4','A4'],
    ['C4', 'F#4','A4'],
    # augmented
    ['C4', 'E4','G#4'],
]
chord_labels_triads = ['CM', 'G#M1st', 'FM2nd', 'Cm', 'Am1st', 'Fm2nd', 'Csus4','Csus2', 'Fsus42nd', 'Cdim','Adim1st', 'F#dim2nd', 'CAug']
empirical_ranking_triads = ['CM', 'Cm', 'FM2nd', 'Fsus42nd', 'G#M1st','Csus2','Csus4', 'Fm2nd','Adim1st','Am1st', 'F#dim2nd','Cdim', 'CAug' ]
empirical_ranking_nums_triads = [1.667,2.407,2.741,2.852,2.889,3.111,3.148,3.481,3.519,3.593,3.667,3.889,5.259]
biggest_df = None
file_path = Path.cwd().parent / 'data_csvs'/ 'all_triad_methods_with_results.csv'

In [7]:
biggest_df = ihm.pipeline_for_interharmonic_normalized_tension_scores(
    note_combinations_array=triads,
    chord_labels_array=chord_labels_triads,
    r_ranges=arrays_of_ranges,
    r_range_names=r_range_methods,
    file_path=file_path)

Now processing 2 harmonics
Now processing [(0.0, 0.125), (0.125, 0.25), (0.25, 0.5), (0.5, 1.5), (1.5, 2.5), (2.5, 3.5), (3.5, 4.5), (4.5, 5.5), (5.5, 6.5), (6.5, 7.5), (7.5, 8.5), (8.5, 9.5), (9.5, 10.5), (10.5, 11.5), (11.5, 12.5)] with ranges all_ranges


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries befo

Now processing [(0.25, 0.5), (0.5, 1.5), (1.5, 2.5), (2.5, 3.5), (3.5, 4.5), (4.5, 5.5), (5.5, 6.5), (6.5, 7.5), (7.5, 8.5), (8.5, 9.5), (9.5, 10.5), (10.5, 11.5), (11.5, 12.5)] with ranges start_from_0.5


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries befo

Now processing [(0.95, 1.1), (1.5, 2.8)] with ranges chan_vanilla


...

c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries befo

Now processing [(0.25, 0.5), (0.5, 1.5), (1.5, 2.5), (2.5, 3.5), (3.5, 4.5), (4.5, 5.5), (5.5, 6.5), (6.5, 7.5), (7.5, 8.5), (8.5, 9.5), (9.5, 10.5), (10.5, 11.5), (11.5, 12.5)] with ranges start_from_0.5


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:757: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries befo

Now processing [(0.95, 1.1), (1.5, 2.8)] with ranges chan_vanilla


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:728: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\interharmonic_module\interharmonic_modulations.py:728: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries befo

13 chords * 18 methods * 31 harmonics =   7254 rows

In [10]:
biggest_df = pd.read_csv('../data_csvs/all_triad_methods_with_results.csv')
biggest_df


note_combination chord_label  \
0            C4,E4,G#4        CAug   
1             C4,F4,A4       FM2nd   
2             C4,E4,A4       Am1st   
3             C4,E4,G4          CM   
4           C4,D#4,G#4      G#M1st   
...                ...         ...   
10876        C4,D#4,A4     Adim1st   
10877        C4,F#4,A4    F#dim2nd   
10878         C4,E4,G4          CM   
10879        C4,D#4,G4          Cm   
10880       C4,D#4,F#4        Cdim   

                              raw_values_per_combination  \
0      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.300000000000...   
1      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.300000000000...   
2      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.300000000000...   
3      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.300000000000...   
4      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.30000000000000004...   
...                                                  ...   
10876                                [[6, 92], [18, 65]]   
10877                                [[18, 65], [6, 92]]   
10878                                [[13, 76], [6, 92]]   
10879                                [[6, 92], [13, 76]]   
10880                                 [[6, 92], [6, 92]]   

      weighted_modulations_per_region_in_note_combinations  \
0      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...     
1      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...     
2      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...     
3      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,...     
4      [[0.0, 0.0, 0.0, 0.0, 0.0, 0.21000000000000002...     
...                                                  ...     
10876                                                NaN     
10877                                                NaN     
10878                                                NaN     
10879                                                NaN     
10880                                                NaN     

      weighted_sum_per_region_normalized_tension_value  \
0                                      [0.0, 0.0, 0.0]   
1                      [0.0, 0.17499999999999996, 0.0]   
2                      [0.0, 0.17499999999999996, 0.0]   
3                                     [0.0, 0.0, 0.35]   
4                                     [0.35, 0.0, 0.0]   
...                                                ...   
10876                                              NaN   
10877                                              NaN   
10878                                              NaN   
10879                                              NaN   
10880                                              NaN   

       raw_t_score_summed_only_modulations  \
0                                      1.8   
1                                      1.6   
2                                      1.6   
3                                      1.8   
4                                      1.8   
...                                    ...   
10876                                181.0   
10877                                181.0   
10878                                187.0   
10879                                187.0   
10880                                196.0   

       raw_t_score_summed_using_weighted_normalized_value  \
0                                                  0.000    
1                                                  0.175    
2                                                  0.175    
3                                                  0.350    
4                                                  0.350    
...                                                  ...    
10876                                                NaN    
10877                                                NaN    
10878                                                NaN    
10879                                                NaN    
10880                                                NaN    

       raw_t_score_summed_using_weighted_modulations_no_norm  \
0                                   

In [9]:
biggest_df[(biggest_df['r_names_used']=='chan_vanilla')& (biggest_df['harmonics_considered']==14)& (biggest_df['distributive']!= False)]

note_combination chord_label   raw_values_per_combination  \
4524        C4,F4,A#4    Fsus42nd  [[0, 13], [0, 15], [0, 13]]   
4525         C4,F4,A4       FM2nd  [[0, 13], [0, 14], [4, 15]]   
4526         C4,E4,A4       Am1st  [[4, 15], [0, 14], [0, 13]]   
4527         C4,F4,G4       Csus4  [[0, 13], [0, 11], [0, 22]]   
4528         C4,D4,G4       Csus2  [[0, 22], [0, 11], [0, 13]]   
4529         C4,E4,G4          CM  [[4, 15], [0, 11], [0, 22]]   
4530       C4,D#4,G#4      G#M1st  [[0, 22], [4, 13], [0, 13]]   
4531        C4,D#4,G4          Cm  [[0, 22], [0, 11], [4, 15]]   
4532        C4,F4,G#4       Fm2nd  [[0, 13], [4, 13], [0, 22]]   
4533        C4,E4,G#4        CAug  [[4, 15], [4, 13], [4, 15]]   
4534        C4,D#4,A4     Adim1st  [[0, 22], [0, 14], [7, 13]]   
4535        C4,F#4,A4    F#dim2nd  [[7, 13], [0, 14], [0, 22]]   
4536       C4,D#4,F#4        Cdim  [[0, 22], [7, 13], [0, 22]]   
4537        C4,F4,A#4    Fsus42nd  [[0, 13], [0, 15], [0, 13]]   
4538         C4,F4,A4       FM2nd  [[0, 13], [0, 14], [4, 15]]   
4539         C4,E4,A4       Am1st  [[4, 15], [0, 14], [0, 13]]   
4540         C4,F4,G4       Csus4  [[0, 13], [0, 11], [0, 22]]   
4541         C4,D4,G4       Csus2  [[0, 22], [0, 11], [0, 13]]   
4542         C4,E4,G4          CM  [[4, 15], [0, 11], [0, 22]]   
4543       C4,D#4,G#4      G#M1st  [[0, 22], [4, 13], [0, 13]]   
4544        C4,D#4,G4          Cm  [[0, 22], [0, 11], [4, 15]]   
4545        C4,F4,G#4       Fm2nd  [[0, 13], [4, 13], [0, 22]]   
4546        C4,E4,G#4        CAug  [[4, 15], [4, 13], [4, 15]]   
4547        C4,D#4,A4     Adim1st  [[0, 22], [0, 14], [7, 13]]   
4548        C4,F#4,A4    F#dim2nd  [[7, 13], [0, 14], [0, 22]]   
4549       C4,D#4,F#4        Cdim  [[0, 22], [7, 13], [0, 22]]   
4550        C4,F4,A#4    Fsus42nd           [[0, 13], [0, 13]]   
4551         C4,F4,A4       FM2nd           [[0, 13], [4, 15]]   
4552         C4,E4,A4       Am1st           [[4, 15], [0, 13]]   
4553       C4,D#4,G#4      G#M1st           [[0, 22], [0, 13]]   
4554        C4,F4,G#4       Fm2nd           [[0, 13], [0, 22]]   
4555         C4,F4,G4       Csus4           [[0, 13], [0, 22]]   
4556         C4,D4,G4       Csus2           [[0, 22], [0, 13]]   
4557        C4,E4,G#4        CAug           [[4, 15], [4, 15]]   
4558         C4,E4,G4          CM           [[4, 15], [0, 22]]   
4559        C4,D#4,G4          Cm           [[0, 22], [4, 15]]   
4560        C4,D#4,A4     Adim1st           [[0, 22], [7, 13]]   
4561        C4,F#4,A4    F#dim2nd           [[7, 13], [0, 22]]   
4562       C4,D#4,F#4        Cdim           [[0, 22], [0, 22]]   

     weighted_modulations_per_region_in_note_combinations  \
4524                                                NaN     
4525                                                NaN     
4526                                                NaN     
4527                                                NaN     
4528                                                NaN     
4529                                                NaN     
4530                                                NaN     
4531                                                NaN     
4532                                                NaN     
4533                                                NaN     
4534                                                NaN     
4535                                                NaN     
4536                                                NaN     
4537                                                NaN     
4538                                                NaN     
4539                                                NaN     
4540                                                NaN     
4541                                                NaN     
4542                                                NaN     
4543                                                NaN     
4544                                                NaN     
4545                  

In [11]:
method_columns = ['method','r_names_used','distributive','weights_on_harmonics','weights_on_regions']
print(biggest_df.columns)
biggest_df[method_columns].drop_duplicates()


Index(['note_combination', 'chord_label', 'raw_values_per_combination',
       'weighted_modulations_per_region_in_note_combinations',
       'weighted_sum_per_region_normalized_tension_value',
       'raw_t_score_summed_only_modulations',
       'raw_t_score_summed_using_weighted_normalized_value',
       'raw_t_score_summed_using_weighted_modulations_no_norm',
       'normed_values_only_modulations',
       'normed_values_normed_weighted_modulations',
       'normed_values_weighted_modulations_only', 'method', 'r_ranges_used',
       'r_names_used', 'distributive', 'harmonics_considered',
       'weights_on_harmonics', 'weights_on_regions', 'weights_for_regions'],
      dtype='object')


method    r_names_used            distributive  \
0    Experimental_methods       all_ranges     weight_interval_sum   
13   Experimental_methods       all_ranges     weight_interval_sum   
26   Experimental_methods       all_ranges     weight_interval_sum   
39   Experimental_methods       all_ranges     weight_interval_sum   
52   Experimental_methods       all_ranges  all_modulations_weight   
65   Experimental_methods       all_ranges  all_modulations_weight   
78   Experimental_methods       all_ranges  all_modulations_weight   
91   Experimental_methods       all_ranges  all_modulations_weight   
104  Experimental_methods       all_ranges                   False   
117  Experimental_methods       all_ranges                   False   
130  Experimental_methods       all_ranges                   False   
143  Experimental_methods       all_ranges                   False   
156  Experimental_methods   start_from_0.5     weight_interval_sum   
169  Experimental_methods   start_from_0.5     weight_interval_sum   
182  Experimental_methods   start_from_0.5     weight_interval_sum   
195  Experimental_methods   start_from_0.5     weight_interval_sum   
208  Experimental_methods   start_from_0.5  all_modulations_weight   
221  Experimental_methods   start_from_0.5  all_modulations_weight   
234  Experimental_methods   start_from_0.5  all_modulations_weight   
247  Experimental_methods   start_from_0.5  all_modulations_weight   
260  Experimental_methods   start_from_0.5                   False   
273  Experimental_methods   start_from_0.5                   False   
286  Experimental_methods   start_from_0.5                   False   
299  Experimental_methods   start_from_0.5                   False   
312  Chan's method Vanilla    chan_vanilla     weight_interval_sum   
325  Chan's method Vanilla    chan_vanilla  all_modulations_weight   
338  Chan's method Vanilla    chan_vanilla                   False   

     weights_on_harmonics  weights_on_regions  
0                    True                True  
13                   True               False  
26                  False                True  
39                  False               False  
52                   True                True  
65                   True               False  
78                  False                True  
91                  False               False  
104                  True                True  
117                  True               False  
130                 False                True  
143                 False               False  
156                  True                True  
169                  True               False  
182                 False                True  
195                 False               False  
208                  True                True  
221                  True               False  
234                 False                True  
247                 False               False  
260                  True                True  
273                  True               False  
286                 False                True  
299                 False               False  
312                 False               False  
325                 False               False  
338                 False               False

18 methods * 31 harmonics * 3 normed evaluations  = 1674 rows

In [12]:
new_df_with_explicit_ratings  = break_into_different_rankings(biggest_df,empirical_ranking=empirical_ranking_triads,numbered_ranking=empirical_ranking_nums_triads, method_columns=method_columns,x_axis='harmonics_considered', normed_values_columns=normed_values_columns)
new_df_with_explicit_ratings['compared_with']='numbered_rankings'

df_with_no_explicit_ratings  = break_into_different_rankings(biggest_df,empirical_ranking=empirical_ranking_triads, method_columns=method_columns,x_axis='harmonics_considered', normed_values_columns=normed_values_columns)
df_with_no_explicit_ratings['compared_with']='ranking_order'

df_to_use = pd.concat([new_df_with_explicit_ratings, df_with_no_explicit_ratings], ignore_index=True)
df_to_use

Processing new method combination:
	method: Experimental_methods 
	r_names_used: all_ranges
	distributive: weight_interval_sum
	weights_on_harmonics: True
	weights_on_regions: True
Cantidad de filas para este metodo: 403
----------------------------------
               method r_names_used        distributive  weights_on_harmonics  weights_on_regions                  normed_column  harmonics_considered  correlation  p_value                                           final_ranking_correlate
Experimental_methods    all_ranges weight_interval_sum                  True                True normed_values_only_modulations                     2    -0.025652 0.933705 [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 1.0, 1.0]
               method r_names_used        distributive  weights_on_harmonics  weights_on_regions                           normed_column  harmonics_considered  correlation  p_value                                                                                        

C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWar

               method r_names_used distributive  weights_on_harmonics  weights_on_regions                             normed_column  harmonics_considered  correlation  p_value                                                                                                                                                                                                 final_ranking_correlate
Experimental_methods    all_ranges        False                  True                True normed_values_normed_weighted_modulations                     9     0.090429 0.768914 [0.4135327385650801, 0.4135327385650801, 0.0869949538380553, 0.0, 0.3334631595351118, 0.4457786072033309, 0.4457786072033309, 0.3334631595351118, 1.0, 0.0869949538380553, 1.0, 0.6566657774909007, 0.1710779040143515]
               method r_names_used distributive  weights_on_harmonics  weights_on_regions                  normed_column  harmonics_considered  correlation  p_value                                                    

C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)


               method r_names_used distributive  weights_on_harmonics  weights_on_regions                  normed_column  harmonics_considered  correlation  p_value                                                                                                                                                                                                             final_ranking_correlate
Experimental_methods    all_ranges        False                  True               False normed_values_only_modulations                     9     0.059855 0.845991 [0.9583333333333316, 0.9583333333333316, 0.500000000000002, 0.0, 0.4583333333333335, 0.4583333333333335, 0.4583333333333335, 0.4583333333333335, 0.2361111111111068, 0.500000000000002, 0.2361111111111068, 0.916666666666667, 1.0]
               method r_names_used distributive  weights_on_harmonics  weights_on_regions                           normed_column  harmonics_considered  correlation  p_value                                         

...

C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWar

               method   r_names_used distributive  weights_on_harmonics  weights_on_regions                           normed_column  harmonics_considered  correlation  p_value                                                                                                                                                                                               final_ranking_correlate
Experimental_methods  start_from_0.5        False                 False                True normed_values_weighted_modulations_only                     9     0.356888 0.231287 [0.4830917874396135, 0.4830917874396135, 0.1642512077294683, 0.0, 0.3188405797101447, 0.405797101449275, 0.405797101449275, 0.3188405797101447, 1.0, 0.1642512077294683, 1.0, 0.6376811594202896, 0.3285024154589371]
               method   r_names_used distributive  weights_on_harmonics  weights_on_regions                             normed_column  harmonics_considered  correlation  p_value                                           

C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)
C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2808215392.py:36: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = pearsonr(normalized_values, values_to_correlate)


               method   r_names_used distributive  weights_on_harmonics  weights_on_regions                  normed_column  harmonics_considered  correlation  p_value                                           final_ranking_correlate
Experimental_methods  start_from_0.5        False                 False               False normed_values_only_modulations                     4     0.197386 0.518032 [0.5, 0.5, 0.5, 0.0, 0.0, 0.0, 0.0, 0.0, 0.5, 0.5, 0.5, 0.0, 1.0]
               method   r_names_used distributive  weights_on_harmonics  weights_on_regions                           normed_column  harmonics_considered  correlation  p_value                                           final_ranking_correlate
Experimental_methods  start_from_0.5        False                 False               False normed_values_weighted_modulations_only                     4          NaN      NaN [nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]
               method   r_names_used distributive 

method  r_names_used         distributive  \
0     Experimental_methods     all_ranges  weight_interval_sum   
1     Experimental_methods     all_ranges  weight_interval_sum   
2     Experimental_methods     all_ranges  weight_interval_sum   
3     Experimental_methods     all_ranges  weight_interval_sum   
4     Experimental_methods     all_ranges  weight_interval_sum   
...                     ...           ...                  ...   
5017  Chan's method Vanilla  chan_vanilla                False   
5018  Chan's method Vanilla  chan_vanilla                False   
5019  Chan's method Vanilla  chan_vanilla                False   
5020  Chan's method Vanilla  chan_vanilla                False   
5021  Chan's method Vanilla  chan_vanilla                False   

      weights_on_harmonics  weights_on_regions  \
0                     True                True   
1                     True                True   
2                     True                True   
3                     True                True   
4                     True                True   
...                    ...                 ...   
5017                 False               False   
5018                 False               False   
5019                 False               False   
5020                 False               False   
5021                 False               False   

                                  normed_column  harmonics_considered  \
0                normed_values_only_modulations                     2   
1       normed_values_weighted_modulations_only                     2   
2     normed_values_normed_weighted_modulations                     2   
3                normed_values_only_modulations                     3   
4       normed_values_weighted_modulations_only                     3   
...                                         ...                   ...   
5017    normed_values_weighted_modulations_only                    31   
5018  normed_values_normed_weighted_modulations                    31   
5019             normed_values_only_modulations                    32   
5020    normed_values_weighted_modulations_only                    32   
5021  normed_values_normed_weighted_modulations                    32   

      correlation   p_value  \
0       -0.025652  0.933705   
1        0.091125  0.767179   
2        0.073246  0.812035   
3       -0.025652  0.933705   
4        0.220813  0.468478   
...           ...       ...   
5017          NaN       NaN   
5018          NaN       NaN   
5019     0.230926  0.447811   
5020          NaN       NaN   
5021          NaN       NaN   

                                final_ranking_correlate      compared_with  
0     [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...  numbered_rankings  
1     [0.2560975609756097, 0.2560975609756097, 0.085...  numbered_rankings  
2     [0.2560975609756097, 0.2560975609756097, 0.128...  numbered_rankings  
3     [1.0, 1.0, 1.4802973661668697e-15, 1.480297366...  numbered_rankings  
4     [0.115079365079365, 0.115079365079365, 0.02380...  numbered_rankings  
...                                                 ...                ...  
5017  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...      ranking_order  
5018  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...      ranking_order  
5019  [0.8333333333333334, 0.8333333333333334, 0.333...      ranking_order  
5020  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...      ranking_order  
5021  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...      ranking_order  

[5022 rows x 11 columns]

In [13]:
df_to_use[df_to_use['correlation'].isnull()]

method  r_names_used         distributive  \
94    Experimental_methods     all_ranges  weight_interval_sum   
95    Experimental_methods     all_ranges  weight_interval_sum   
97    Experimental_methods     all_ranges  weight_interval_sum   
98    Experimental_methods     all_ranges  weight_interval_sum   
100   Experimental_methods     all_ranges  weight_interval_sum   
...                     ...           ...                  ...   
5015  Chan's method Vanilla  chan_vanilla                False   
5017  Chan's method Vanilla  chan_vanilla                False   
5018  Chan's method Vanilla  chan_vanilla                False   
5020  Chan's method Vanilla  chan_vanilla                False   
5021  Chan's method Vanilla  chan_vanilla                False   

      weights_on_harmonics  weights_on_regions  \
94                    True               False   
95                    True               False   
97                    True               False   
98                    True               False   
100                   True               False   
...                    ...                 ...   
5015                 False               False   
5017                 False               False   
5018                 False               False   
5020                 False               False   
5021                 False               False   

                                  normed_column  harmonics_considered  \
94      normed_values_weighted_modulations_only                     2   
95    normed_values_normed_weighted_modulations                     2   
97      normed_values_weighted_modulations_only                     3   
98    normed_values_normed_weighted_modulations                     3   
100     normed_values_weighted_modulations_only                     4   
...                                         ...                   ...   
5015  normed_values_normed_weighted_modulations                    30   
5017    normed_values_weighted_modulations_only                    31   
5018  normed_values_normed_weighted_modulations                    31   
5020    normed_values_weighted_modulations_only                    32   
5021  normed_values_normed_weighted_modulations                    32   

      correlation  p_value                            final_ranking_correlate  \
94            NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
95            NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
97            NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
98            NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
100           NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
...           ...      ...                                                ...   
5015          NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
5017          NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
5018          NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
5020          NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
5021          NaN      NaN  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   

          compared_with  
94    numbered_rankings  
95    numbered_rankings  
97    numbered_rankings  
98    numbered_rankings  
100   numbered_rankings  
...                 ...  
5015      ranking_order  
5017      ranking_order  
5018      ranking_order  
5020      ranking_order  
5021      ranking_order  

[1924 rows x 11 columns]

3348 rows - (10 methods* 2 methods that have no normed evaluation * 31 harmoics )= rows

In [14]:
df_to_use = df_to_use.dropna()
df_to_use


method  r_names_used         distributive  \
0     Experimental_methods     all_ranges  weight_interval_sum   
1     Experimental_methods     all_ranges  weight_interval_sum   
2     Experimental_methods     all_ranges  weight_interval_sum   
3     Experimental_methods     all_ranges  weight_interval_sum   
4     Experimental_methods     all_ranges  weight_interval_sum   
...                     ...           ...                  ...   
5007  Chan's method Vanilla  chan_vanilla                False   
5010  Chan's method Vanilla  chan_vanilla                False   
5013  Chan's method Vanilla  chan_vanilla                False   
5016  Chan's method Vanilla  chan_vanilla                False   
5019  Chan's method Vanilla  chan_vanilla                False   

      weights_on_harmonics  weights_on_regions  \
0                     True                True   
1                     True                True   
2                     True                True   
3                     True                True   
4                     True                True   
...                    ...                 ...   
5007                 False               False   
5010                 False               False   
5013                 False               False   
5016                 False               False   
5019                 False               False   

                                  normed_column  harmonics_considered  \
0                normed_values_only_modulations                     2   
1       normed_values_weighted_modulations_only                     2   
2     normed_values_normed_weighted_modulations                     2   
3                normed_values_only_modulations                     3   
4       normed_values_weighted_modulations_only                     3   
...                                         ...                   ...   
5007             normed_values_only_modulations                    28   
5010             normed_values_only_modulations                    29   
5013             normed_values_only_modulations                    30   
5016             normed_values_only_modulations                    31   
5019             normed_values_only_modulations                    32   

      correlation   p_value  \
0       -0.025652  0.933705   
1        0.091125  0.767179   
2        0.073246  0.812035   
3       -0.025652  0.933705   
4        0.220813  0.468478   
...           ...       ...   
5007     0.233293  0.443038   
5010     0.215352  0.479825   
5013     0.220942  0.468213   
5016     0.225580  0.458680   
5019     0.230926  0.447811   

                                final_ranking_correlate      compared_with  
0     [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...  numbered_rankings  
1     [0.2560975609756097, 0.2560975609756097, 0.085...  numbered_rankings  
2     [0.2560975609756097, 0.2560975609756097, 0.128...  numbered_rankings  
3     [1.0, 1.0, 1.4802973661668697e-15, 1.480297366...  numbered_rankings  
4     [0.115079365079365, 0.115079365079365, 0.02380...  numbered_rankings  
...                                                 ...                ...  
5007  [0.825, 0.825, 0.325, 0.0, 0.5, 0.4, 0.4, 0.5,...      ranking_order  
5010  [0.782608695652174, 0.782608695652174, 0.28260...      ranking_order  
5013  [0.7708333333333334, 0.7708333333333334, 0.270...      ranking_order  
5016  [0.78, 0.78, 0.28, 0.0, 0.5, 0.34, 0.34, 0.5, ...      ranking_order  
5019  [0.8333333333333334, 0.8333333333333334, 0.333...      ranking_order  

[3098 rows x 11 columns]

## Saving corr csv

In [15]:
df_to_use.to_csv('../data_csvs/ihm_correlation_triads_with_empirical.csv', index=False)

In [21]:
name_conditions(df_to_use)
df_to_use

C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\631205928.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  biggest_df['cleaned_method_name'] = None


method  r_names_used         distributive  \
0     Experimental_methods     all_ranges  weight_interval_sum   
1     Experimental_methods     all_ranges  weight_interval_sum   
2     Experimental_methods     all_ranges  weight_interval_sum   
3     Experimental_methods     all_ranges  weight_interval_sum   
4     Experimental_methods     all_ranges  weight_interval_sum   
...                     ...           ...                  ...   
5007  Chan's method Vanilla  chan_vanilla                False   
5010  Chan's method Vanilla  chan_vanilla                False   
5013  Chan's method Vanilla  chan_vanilla                False   
5016  Chan's method Vanilla  chan_vanilla                False   
5019  Chan's method Vanilla  chan_vanilla                False   

      weights_on_harmonics  weights_on_regions  \
0                     True                True   
1                     True                True   
2                     True                True   
3                     True                True   
4                     True                True   
...                    ...                 ...   
5007                 False               False   
5010                 False               False   
5013                 False               False   
5016                 False               False   
5019                 False               False   

                                  normed_column  harmonics_considered  \
0                normed_values_only_modulations                     2   
1       normed_values_weighted_modulations_only                     2   
2     normed_values_normed_weighted_modulations                     2   
3                normed_values_only_modulations                     3   
4       normed_values_weighted_modulations_only                     3   
...                                         ...                   ...   
5007             normed_values_only_modulations                    28   
5010             normed_values_only_modulations                    29   
5013             normed_values_only_modulations                    30   
5016             normed_values_only_modulations                    31   
5019             normed_values_only_modulations                    32   

      correlation   p_value  \
0       -0.025652  0.933705   
1        0.091125  0.767179   
2        0.073246  0.812035   
3       -0.025652  0.933705   
4        0.220813  0.468478   
...           ...       ...   
5007     0.233293  0.443038   
5010     0.215352  0.479825   
5013     0.220942  0.468213   
5016     0.225580  0.458680   
5019     0.230926  0.447811   

                                final_ranking_correlate      compared_with  \
0     [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...  numbered_rankings   
1     [0.2560975609756097, 0.2560975609756097, 0.085...  numbered_rankings   
2     [0.2560975609756097, 0.2560975609756097, 0.128...  numbered_rankings   
3     [1.0, 1.0, 1.4802973661668697e-15, 1.480297366...  numbered_rankings   
4     [0.115079365079365, 0.115079365079365, 0.02380...  numbered_rankings   
...                                                 ...                ...   
5007  [0.825, 0.825, 0.325, 0.0, 0.5, 0.4, 0.4, 0.5,...      ranking_order   
5010  [0.782608695652174, 0.782608695652174, 0.28260...      ranking_order   
5013  [0.7708333333333334, 0.7708333333333334, 0.270...      ranking_order   
5016  [0.78, 0.78, 0.28, 0.0, 0.5, 0.34, 0.34, 0.5, ...      ranking_order   
5019  [0.8333333333333334, 0.8333333333333334, 0.333...      ranking_order   

     cleaned_method_name  
0               Method E  
1               Method E  
2               Method E  
3               Method E  
4               Method E  
...                  ...  
5007            Method A  
5010            Method A  
5013            Method A  
5016            Method A  
5019            Method A  

[3098 rows x 12 columns]

## cleaning method names

In [22]:
new_df_with_explicit_ratings = df_to_use

In [23]:

new_df_with_explicit_ratings[new_df_with_explicit_ratings['cleaned_method_name']=='Method A']


method  r_names_used         distributive  \
2232  Chan's method Vanilla  chan_vanilla  weight_interval_sum   
2235  Chan's method Vanilla  chan_vanilla  weight_interval_sum   
2238  Chan's method Vanilla  chan_vanilla  weight_interval_sum   
2241  Chan's method Vanilla  chan_vanilla  weight_interval_sum   
2244  Chan's method Vanilla  chan_vanilla  weight_interval_sum   
...                     ...           ...                  ...   
5007  Chan's method Vanilla  chan_vanilla                False   
5010  Chan's method Vanilla  chan_vanilla                False   
5013  Chan's method Vanilla  chan_vanilla                False   
5016  Chan's method Vanilla  chan_vanilla                False   
5019  Chan's method Vanilla  chan_vanilla                False   

      weights_on_harmonics  weights_on_regions  \
2232                 False               False   
2235                 False               False   
2238                 False               False   
2241                 False               False   
2244                 False               False   
...                    ...                 ...   
5007                 False               False   
5010                 False               False   
5013                 False               False   
5016                 False               False   
5019                 False               False   

                       normed_column  harmonics_considered  correlation  \
2232  normed_values_only_modulations                     2    -0.141078   
2235  normed_values_only_modulations                     3     0.102122   
2238  normed_values_only_modulations                     4     0.083453   
2241  normed_values_only_modulations                     5     0.018997   
2244  normed_values_only_modulations                     6     0.103463   
...                              ...                   ...          ...   
5007  normed_values_only_modulations                    28     0.233293   
5010  normed_values_only_modulations                    29     0.215352   
5013  normed_values_only_modulations                    30     0.220942   
5016  normed_values_only_modulations                    31     0.225580   
5019  normed_values_only_modulations                    32     0.230926   

       p_value                            final_ranking_correlate  \
2232  0.645717  [0.5, 0.5, 0.25, 0.25, 0.5, 0.5, 0.5, 0.5, 0.7...   
2235  0.739907  [0.25, 0.25, 0.25, 0.25, 0.5, 0.25, 0.25, 0.5,...   
2238  0.786356  [0.4285714285714285, 0.4285714285714285, 0.142...   
2241  0.950882  [0.4545454545454545, 0.4545454545454545, 0.090...   
2244  0.736601  [0.2727272727272727, 0.2727272727272727, 0.181...   
...        ...                                                ...   
5007  0.443038  [0.825, 0.825, 0.325, 0.0, 0.5, 0.4, 0.4, 0.5,...   
5010  0.479825  [0.782608695652174, 0.782608695652174, 0.28260...   
5013  0.468213  [0.7708333333333334, 0.7708333333333334, 0.270...   
5016  0.458680  [0.78, 0.78, 0.28, 0.0, 0.5, 0.34, 0.34, 0.5, ...   
5019  0.447811  [0.8333333333333334, 0.8333333333333334, 0.333...   

          compared_with cleaned_method_name  
2232  numbered_rankings            Method A  
2235  numbered_rankings            Method A  
2238  numbered_rankings            Method A  
2241  numbered_rankings            Method A  
2244  numbered_rankings            Method A  
...                 ...                 ...  
5007      ranking_order            Method A  
5010      ranking_order            Method A  
5013      ranking_order            Method A  
5016      ranking_order            Method A  
5019      ranking_order            Method A  

[186 rows x 12 columns]

In [24]:
new_df_with_explicit_ratings[new_df_with_explicit_ratings['cleaned_method_name']=='Method B']


method    r_names_used         distributive  \
279   Experimental_methods       all_ranges  weight_interval_sum   
282   Experimental_methods       all_ranges  weight_interval_sum   
285   Experimental_methods       all_ranges  weight_interval_sum   
288   Experimental_methods       all_ranges  weight_interval_sum   
291   Experimental_methods       all_ranges  weight_interval_sum   
...                     ...             ...                  ...   
4728  Experimental_methods   start_from_0.5                False   
4731  Experimental_methods   start_from_0.5                False   
4734  Experimental_methods   start_from_0.5                False   
4737  Experimental_methods   start_from_0.5                False   
4740  Experimental_methods   start_from_0.5                False   

      weights_on_harmonics  weights_on_regions  \
279                  False               False   
282                  False               False   
285                  False               False   
288                  False               False   
291                  False               False   
...                    ...                 ...   
4728                 False               False   
4731                 False               False   
4734                 False               False   
4737                 False               False   
4740                 False               False   

                       normed_column  harmonics_considered  correlation  \
279   normed_values_only_modulations                     2    -0.025652   
282   normed_values_only_modulations                     3    -0.025652   
285   normed_values_only_modulations                     4     0.061247   
288   normed_values_only_modulations                     5     0.282253   
291   normed_values_only_modulations                     6     0.200381   
...                              ...                   ...          ...   
4728  normed_values_only_modulations                    28    -0.074271   
4731  normed_values_only_modulations                    29    -0.052536   
4734  normed_values_only_modulations                    30    -0.103828   
4737  normed_values_only_modulations                    31    -0.104662   
4740  normed_values_only_modulations                    32    -0.035487   

       p_value                            final_ranking_correlate  \
279   0.933705  [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...   
282   0.933705  [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...   
285   0.842448  [0.6666666666666666, 0.6666666666666666, 0.333...   
288   0.350133  [0.5, 0.5, 0.25, 0.0, 0.5, 0.25, 0.25, 0.5, 0....   
291   0.511571  [0.6, 0.6, 0.2, 0.0, 0.6, 0.4, 0.4, 0.6, 0.0, ...   
...        ...                                                ...   
4728  0.809449  [0.9166666666666666, 0.9166666666666666, 0.416...   
4731  0.864657  [0.7857142857142857, 0.7857142857142857, 0.285...   
4734  0.735701  [0.7142857142857143, 0.7142857142857143, 0.214...   
4737  0.733647  [0.7857142857142857, 0.7857142857142857, 0.285...   
4740  0.908371  [0.875, 0.875, 0.375, 0.0, 0.5, 0.625, 0.625, ...   

          compared_with cleaned_method_name  
279   numbered_rankings            Method B  
282   numbered_rankings            Method B  
285   numbered_rankings            Method B  
288   numbered_rankings            Method B  
291   numbered_rankings            Method B  
...                 ...                 ...  
4728      ranking_order            Method B  
4731      ranking_order            Method B  
4734      ranking_order            Method B  
4737      ranking_order            Method B  
4740      ranking_order            Method B  

[364 rows x 12 columns]

In [25]:
new_df_with_explicit_ratings[new_df_with_explicit_ratings['cleaned_method_name']=='Method C']


method    r_names_used         distributive  \
186   Experimental_methods       all_ranges  weight_interval_sum   
187   Experimental_methods       all_ranges  weight_interval_sum   
188   Experimental_methods       all_ranges  weight_interval_sum   
189   Experimental_methods       all_ranges  weight_interval_sum   
190   Experimental_methods       all_ranges  weight_interval_sum   
...                     ...             ...                  ...   
4645  Experimental_methods   start_from_0.5                False   
4646  Experimental_methods   start_from_0.5                False   
4647  Experimental_methods   start_from_0.5                False   
4648  Experimental_methods   start_from_0.5                False   
4649  Experimental_methods   start_from_0.5                False   

      weights_on_harmonics  weights_on_regions  \
186                  False                True   
187                  False                True   
188                  False                True   
189                  False                True   
190                  False                True   
...                    ...                 ...   
4645                 False                True   
4646                 False                True   
4647                 False                True   
4648                 False                True   
4649                 False                True   

                                  normed_column  harmonics_considered  \
186              normed_values_only_modulations                     2   
187     normed_values_weighted_modulations_only                     2   
188   normed_values_normed_weighted_modulations                     2   
189              normed_values_only_modulations                     3   
190     normed_values_weighted_modulations_only                     3   
...                                         ...                   ...   
4645    normed_values_weighted_modulations_only                    31   
4646  normed_values_normed_weighted_modulations                    31   
4647             normed_values_only_modulations                    32   
4648    normed_values_weighted_modulations_only                    32   
4649  normed_values_normed_weighted_modulations                    32   

      correlation   p_value  \
186     -0.025652  0.933705   
187      0.103419  0.736711   
188      0.091450  0.766370   
189     -0.025652  0.933705   
190      0.314383  0.295498   
...           ...       ...   
4645     0.163944  0.592517   
4646     0.199336  0.513821   
4647    -0.035487  0.908371   
4648     0.159274  0.603241   
4649     0.184771  0.545633   

                                final_ranking_correlate      compared_with  \
186   [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...  numbered_rankings   
187   [0.2413793103448275, 0.2413793103448275, 0.120...  numbered_rankings   
188   [0.2413793103448275, 0.2413793103448275, 0.160...  numbered_rankings   
189   [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...  numbered_rankings   
190   [0.0, 0.0, 0.09375, 0.25, 0.2031250000000001, ...  numbered_rankings   
...                                                 ...                ...   
4645  [0.740196078431372, 0.740196078431372, 0.24019...      ranking_order   
4646  [0.7357746731259136, 0.7357746731259136, 0.235...      ranking_order   
4647  [0.875, 0.875, 0.375, 0.0, 0.5, 0.625, 0.625, ...      ranking_order   
4648  [0.7500000000000007, 0.7500000000000007, 0.249...      ranking_order   
4649  [0.7330553663663887, 0.7330553663663887, 0.233...      ranking_order   

     cleaned_method_name  
186             Method C  
187             Method C  
188             Method C  
189             Method C  
190             Method C  
...                  ...  
4645            Method C  
4646            Method C  
4647            Method C  
4648            Method C  
4649            Method C  

[1092 rows x 12 columns]

removing wrong evaluations, distributive (2) * 2 ranges * 31 harmonics * 2 normalizations. <br>
if taking only normalizations = 248

In [26]:
new_df_with_explicit_ratings[(new_df_with_explicit_ratings['cleaned_method_name']=='Method C') & (new_df_with_explicit_ratings['normed_column']!='normed_values_normed_weighted_modulations')]

method    r_names_used         distributive  \
186   Experimental_methods       all_ranges  weight_interval_sum   
187   Experimental_methods       all_ranges  weight_interval_sum   
189   Experimental_methods       all_ranges  weight_interval_sum   
190   Experimental_methods       all_ranges  weight_interval_sum   
192   Experimental_methods       all_ranges  weight_interval_sum   
...                     ...             ...                  ...   
4642  Experimental_methods   start_from_0.5                False   
4644  Experimental_methods   start_from_0.5                False   
4645  Experimental_methods   start_from_0.5                False   
4647  Experimental_methods   start_from_0.5                False   
4648  Experimental_methods   start_from_0.5                False   

      weights_on_harmonics  weights_on_regions  \
186                  False                True   
187                  False                True   
189                  False                True   
190                  False                True   
192                  False                True   
...                    ...                 ...   
4642                 False                True   
4644                 False                True   
4645                 False                True   
4647                 False                True   
4648                 False                True   

                                normed_column  harmonics_considered  \
186            normed_values_only_modulations                     2   
187   normed_values_weighted_modulations_only                     2   
189            normed_values_only_modulations                     3   
190   normed_values_weighted_modulations_only                     3   
192            normed_values_only_modulations                     4   
...                                       ...                   ...   
4642  normed_values_weighted_modulations_only                    30   
4644           normed_values_only_modulations                    31   
4645  normed_values_weighted_modulations_only                    31   
4647           normed_values_only_modulations                    32   
4648  normed_values_weighted_modulations_only                    32   

      correlation   p_value  \
186     -0.025652  0.933705   
187      0.103419  0.736711   
189     -0.025652  0.933705   
190      0.314383  0.295498   
192      0.061247  0.842448   
...           ...       ...   
4642     0.176313  0.564482   
4644    -0.104662  0.733647   
4645     0.163944  0.592517   
4647    -0.035487  0.908371   
4648     0.159274  0.603241   

                                final_ranking_correlate      compared_with  \
186   [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...  numbered_rankings   
187   [0.2413793103448275, 0.2413793103448275, 0.120...  numbered_rankings   
189   [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...  numbered_rankings   
190   [0.0, 0.0, 0.09375, 0.25, 0.2031250000000001, ...  numbered_rankings   
192   [0.6666666666666666, 0.6666666666666666, 0.333...  numbered_rankings   
...                                                 ...                ...   
4642  [0.728426395939085, 0.728426395939085, 0.22842...      ranking_order   
4644  [0.7857142857142857, 0.7857142857142857, 0.285...      ranking_order   
4645  [0.740196078431372, 0.740196078431372, 0.24019...      ranking_order   
4647  [0.875, 0.875, 0.375, 0.0, 0.5, 0.625, 0.625, ...      ranking_order   
4648  [0.7500000000000007, 0.7500000000000007, 0.249...      ranking_order   

     cleaned_method_name  
186             Method C  
187             Method C  
189             Method C  
190             Method C  
192             Method C  
...                  ...  
4642            Method C  
4644            Method C  
4645            Method C  
4647            Method C  
4648            Method C  

[728 rows x 12 columns]

In [27]:
new_df_with_explicit_ratings.drop(new_df_with_explicit_ratings[(new_df_with_explicit_ratings['cleaned_method_name']=='Method C') & (new_df_with_explicit_ratings['normed_column']!='normed_values_normed_weighted_modulations')].index, inplace=True)
new_df_with_explicit_ratings[new_df_with_explicit_ratings['cleaned_method_name']=='Method C']


C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\949102317.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df_with_explicit_ratings.drop(new_df_with_explicit_ratings[(new_df_with_explicit_ratings['cleaned_method_name']=='Method C') & (new_df_with_explicit_ratings['normed_column']!='normed_values_normed_weighted_modulations')].index, inplace=True)


method    r_names_used         distributive  \
188   Experimental_methods       all_ranges  weight_interval_sum   
191   Experimental_methods       all_ranges  weight_interval_sum   
194   Experimental_methods       all_ranges  weight_interval_sum   
197   Experimental_methods       all_ranges  weight_interval_sum   
200   Experimental_methods       all_ranges  weight_interval_sum   
...                     ...             ...                  ...   
4637  Experimental_methods   start_from_0.5                False   
4640  Experimental_methods   start_from_0.5                False   
4643  Experimental_methods   start_from_0.5                False   
4646  Experimental_methods   start_from_0.5                False   
4649  Experimental_methods   start_from_0.5                False   

      weights_on_harmonics  weights_on_regions  \
188                  False                True   
191                  False                True   
194                  False                True   
197                  False                True   
200                  False                True   
...                    ...                 ...   
4637                 False                True   
4640                 False                True   
4643                 False                True   
4646                 False                True   
4649                 False                True   

                                  normed_column  harmonics_considered  \
188   normed_values_normed_weighted_modulations                     2   
191   normed_values_normed_weighted_modulations                     3   
194   normed_values_normed_weighted_modulations                     4   
197   normed_values_normed_weighted_modulations                     5   
200   normed_values_normed_weighted_modulations                     6   
...                                         ...                   ...   
4637  normed_values_normed_weighted_modulations                    28   
4640  normed_values_normed_weighted_modulations                    29   
4643  normed_values_normed_weighted_modulations                    30   
4646  normed_values_normed_weighted_modulations                    31   
4649  normed_values_normed_weighted_modulations                    32   

      correlation   p_value  \
188      0.091450  0.766370   
191      0.304892  0.311097   
194      0.235359  0.438893   
197      0.084429  0.783909   
200      0.141604  0.644474   
...           ...       ...   
4637     0.241344  0.426994   
4640     0.220459  0.469211   
4643     0.211066  0.488817   
4646     0.199336  0.513821   
4649     0.184771  0.545633   

                                final_ranking_correlate      compared_with  \
188   [0.2413793103448275, 0.2413793103448275, 0.160...  numbered_rankings   
191   [0.0, 0.0, 0.1473214285714286, 0.3348214285714...  numbered_rankings   
194   [0.0934707903780069, 0.0934707903780068, 0.046...  numbered_rankings   
197   [0.2441983122362868, 0.2441983122362868, 0.105...  numbered_rankings   
200   [0.2006606110652351, 0.2006606110652351, 0.140...  numbered_rankings   
...                                                 ...                ...   
4637  [0.7055088942063205, 0.7055088942063205, 0.206...      ranking_order   
4640  [0.7239939309618602, 0.7239939309618602, 0.224...      ranking_order   
4643  [0.7327057450998496, 0.7327057450998496, 0.232...      ranking_order   
4646  [0.7357746731259136, 0.7357746731259136, 0.235...      ranking_order   
4649  [0.7330553663663887, 0.7330553663663887, 0.233...      ranking_order   

     cleaned_method_name  
188             Method C  
191             Method C  
194             Method C  
197             Method C  
200             Method C  
...                  ...  
4637            Method C  
4640            Method C  
4643            Method C  
4646            Method C  
4649            Method C  

[364 rows x 12 columns]

In [28]:
new_df_with_explicit_ratings[new_df_with_explicit_ratings['cleaned_method_name']=='Method D']


method    r_names_used         distributive  \
93    Experimental_methods       all_ranges  weight_interval_sum   
96    Experimental_methods       all_ranges  weight_interval_sum   
99    Experimental_methods       all_ranges  weight_interval_sum   
102   Experimental_methods       all_ranges  weight_interval_sum   
105   Experimental_methods       all_ranges  weight_interval_sum   
...                     ...             ...                  ...   
4542  Experimental_methods   start_from_0.5                False   
4545  Experimental_methods   start_from_0.5                False   
4548  Experimental_methods   start_from_0.5                False   
4551  Experimental_methods   start_from_0.5                False   
4554  Experimental_methods   start_from_0.5                False   

      weights_on_harmonics  weights_on_regions  \
93                    True               False   
96                    True               False   
99                    True               False   
102                   True               False   
105                   True               False   
...                    ...                 ...   
4542                  True               False   
4545                  True               False   
4548                  True               False   
4551                  True               False   
4554                  True               False   

                       normed_column  harmonics_considered  correlation  \
93    normed_values_only_modulations                     2    -0.025652   
96    normed_values_only_modulations                     3    -0.025652   
99    normed_values_only_modulations                     4     0.000632   
102   normed_values_only_modulations                     5     0.084033   
105   normed_values_only_modulations                     6     0.066205   
...                              ...                   ...          ...   
4542  normed_values_only_modulations                    28    -0.009968   
4545  normed_values_only_modulations                    29    -0.009481   
4548  normed_values_only_modulations                    30    -0.013897   
4551  normed_values_only_modulations                    31    -0.016648   
4554  normed_values_only_modulations                    32    -0.005261   

       p_value                            final_ranking_correlate  \
93    0.933705  [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...   
96    0.933705  [1.0, 1.0, 1.4802973661668697e-15, 1.480297366...   
99    0.998365  [0.8571428571428575, 0.8571428571428575, 0.142...   
102   0.784900  [0.8200000000000001, 0.8200000000000001, 0.199...   
105   0.829854  [0.8411764705882353, 0.8411764705882353, 0.176...   
...        ...                                                ...   
4542  0.974219  [0.842014220317222, 0.842014220317222, 0.34201...   
4545  0.975477  [0.8207673285658107, 0.8207673285658107, 0.320...   
4548  0.964060  [0.8097812952321366, 0.8097812952321366, 0.309...   
4551  0.956952  [0.8099073970070217, 0.8099073970070217, 0.309...   
4554  0.986392  [0.8154123466833719, 0.8154123466833719, 0.315...   

          compared_with cleaned_method_name  
93    numbered_rankings            Method D  
96    numbered_rankings            Method D  
99    numbered_rankings            Method D  
102   numbered_rankings            Method D  
105   numbered_rankings            Method D  
...                 ...                 ...  
4542      ranking_order            Method D  
4545      ranking_order            Method D  
4548      ranking_order            Method D  
4551      ranking_order            Method D  
4554      ranking_order            Method D  

[364 rows x 12 columns]

In [29]:
new_df_with_explicit_ratings[new_df_with_explicit_ratings['cleaned_method_name']=='Method E']


method    r_names_used         distributive  \
0     Experimental_methods       all_ranges  weight_interval_sum   
1     Experimental_methods       all_ranges  weight_interval_sum   
2     Experimental_methods       all_ranges  weight_interval_sum   
3     Experimental_methods       all_ranges  weight_interval_sum   
4     Experimental_methods       all_ranges  weight_interval_sum   
...                     ...             ...                  ...   
4459  Experimental_methods   start_from_0.5                False   
4460  Experimental_methods   start_from_0.5                False   
4461  Experimental_methods   start_from_0.5                False   
4462  Experimental_methods   start_from_0.5                False   
4463  Experimental_methods   start_from_0.5                False   

      weights_on_harmonics  weights_on_regions  \
0                     True                True   
1                     True                True   
2                     True                True   
3                     True                True   
4                     True                True   
...                    ...                 ...   
4459                  True                True   
4460                  True                True   
4461                  True                True   
4462                  True                True   
4463                  True                True   

                                  normed_column  harmonics_considered  \
0                normed_values_only_modulations                     2   
1       normed_values_weighted_modulations_only                     2   
2     normed_values_normed_weighted_modulations                     2   
3                normed_values_only_modulations                     3   
4       normed_values_weighted_modulations_only                     3   
...                                         ...                   ...   
4459    normed_values_weighted_modulations_only                    31   
4460  normed_values_normed_weighted_modulations                    31   
4461             normed_values_only_modulations                    32   
4462    normed_values_weighted_modulations_only                    32   
4463  normed_values_normed_weighted_modulations                    32   

      correlation   p_value  \
0       -0.025652  0.933705   
1        0.091125  0.767179   
2        0.073246  0.812035   
3       -0.025652  0.933705   
4        0.220813  0.468478   
...           ...       ...   
4459     0.284825  0.345570   
4460     0.307617  0.306572   
4461    -0.005261  0.986392   
4462     0.283084  0.348655   
4463     0.306052  0.309166   

                                final_ranking_correlate      compared_with  \
0     [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...  numbered_rankings   
1     [0.2560975609756097, 0.2560975609756097, 0.085...  numbered_rankings   
2     [0.2560975609756097, 0.2560975609756097, 0.128...  numbered_rankings   
3     [1.0, 1.0, 1.4802973661668697e-15, 1.480297366...  numbered_rankings   
4     [0.115079365079365, 0.115079365079365, 0.02380...  numbered_rankings   
...                                                 ...                ...   
4459  [0.6119867383165741, 0.6119867383165741, 0.151...      ranking_order   
4460  [0.4624320903935539, 0.4624320903935539, 0.094...      ranking_order   
4461  [0.8154123466833719, 0.8154123466833719, 0.315...      ranking_order   
4462  [0.6228057699507158, 0.6228057699507158, 0.157...      ranking_order   
4463  [0.4687876084072221, 0.4687876084072221, 0.097...      ranking_order   

     cleaned_method_name  
0               Method E  
1               Method E  
2               Method E  
3               Method E  
4               Method E  
...                  ...  
4459            Method E  
4460            Method E  
4461            Method E  
4462            Method E  
4463            Method E  

[1092 rows x 12 columns]

In [30]:
new_df_with_explicit_ratings.drop(new_df_with_explicit_ratings[(new_df_with_explicit_ratings['cleaned_method_name']=='Method E') & (new_df_with_explicit_ratings['normed_column']!='normed_values_normed_weighted_modulations')].index, inplace=True)
new_df_with_explicit_ratings[new_df_with_explicit_ratings['cleaned_method_name']=='Method E']

C:\Users\gabri\AppData\Local\Temp\ipykernel_35596\2865218100.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df_with_explicit_ratings.drop(new_df_with_explicit_ratings[(new_df_with_explicit_ratings['cleaned_method_name']=='Method E') & (new_df_with_explicit_ratings['normed_column']!='normed_values_normed_weighted_modulations')].index, inplace=True)


method    r_names_used         distributive  \
2     Experimental_methods       all_ranges  weight_interval_sum   
5     Experimental_methods       all_ranges  weight_interval_sum   
8     Experimental_methods       all_ranges  weight_interval_sum   
11    Experimental_methods       all_ranges  weight_interval_sum   
14    Experimental_methods       all_ranges  weight_interval_sum   
...                     ...             ...                  ...   
4451  Experimental_methods   start_from_0.5                False   
4454  Experimental_methods   start_from_0.5                False   
4457  Experimental_methods   start_from_0.5                False   
4460  Experimental_methods   start_from_0.5                False   
4463  Experimental_methods   start_from_0.5                False   

      weights_on_harmonics  weights_on_regions  \
2                     True                True   
5                     True                True   
8                     True                True   
11                    True                True   
14                    True                True   
...                    ...                 ...   
4451                  True                True   
4454                  True                True   
4457                  True                True   
4460                  True                True   
4463                  True                True   

                                  normed_column  harmonics_considered  \
2     normed_values_normed_weighted_modulations                     2   
5     normed_values_normed_weighted_modulations                     3   
8     normed_values_normed_weighted_modulations                     4   
11    normed_values_normed_weighted_modulations                     5   
14    normed_values_normed_weighted_modulations                     6   
...                                         ...                   ...   
4451  normed_values_normed_weighted_modulations                    28   
4454  normed_values_normed_weighted_modulations                    29   
4457  normed_values_normed_weighted_modulations                    30   
4460  normed_values_normed_weighted_modulations                    31   
4463  normed_values_normed_weighted_modulations                    32   

      correlation   p_value  \
2        0.073246  0.812035   
5        0.209963  0.491145   
8        0.188181  0.538112   
11       0.118554  0.699684   
14       0.142702  0.641881   
...           ...       ...   
4451     0.308309  0.305429   
4454     0.307145  0.307353   
4457     0.306794  0.307934   
4460     0.307617  0.306572   
4463     0.306052  0.309166   

                                final_ranking_correlate      compared_with  \
2     [0.2560975609756097, 0.2560975609756097, 0.128...  numbered_rankings   
5     [0.1150793650793649, 0.1150793650793649, 0.086...  numbered_rankings   
8     [0.1479729869271598, 0.1479729869271598, 0.076...  numbered_rankings   
11    [0.2134432237560609, 0.2134432237560609, 0.102...  numbered_rankings   
14    [0.1981854451027551, 0.198185445102755, 0.1182...  numbered_rankings   
...                                                 ...                ...   
4451  [0.4413607802118836, 0.4413607802118836, 0.083...      ranking_order   
4454  [0.4547949207508316, 0.4547949207508316, 0.089...      ranking_order   
4457  [0.4550765686801244, 0.4550765686801244, 0.090...      ranking_order   
4460  [0.4624320903935539, 0.4624320903935539, 0.094...      ranking_order   
4463  [0.4687876084072221, 0.4687876084072221, 0.097...      ranking_order   

     cleaned_method_name  
2               Method E  
5               Method E  
8               Method E  
11              Method E  
14              Method E  
...                  ...  
4451            Method E  
4454            Method E  
4457            Method E  
4460            Method E  
4463            Method E  

[364 rows x 12 columns]

18 methods * 31 harmonics  (what we want :)

In [31]:
new_df_with_explicit_ratings

method  r_names_used         distributive  \
2     Experimental_methods     all_ranges  weight_interval_sum   
5     Experimental_methods     all_ranges  weight_interval_sum   
8     Experimental_methods     all_ranges  weight_interval_sum   
11    Experimental_methods     all_ranges  weight_interval_sum   
14    Experimental_methods     all_ranges  weight_interval_sum   
...                     ...           ...                  ...   
5007  Chan's method Vanilla  chan_vanilla                False   
5010  Chan's method Vanilla  chan_vanilla                False   
5013  Chan's method Vanilla  chan_vanilla                False   
5016  Chan's method Vanilla  chan_vanilla                False   
5019  Chan's method Vanilla  chan_vanilla                False   

      weights_on_harmonics  weights_on_regions  \
2                     True                True   
5                     True                True   
8                     True                True   
11                    True                True   
14                    True                True   
...                    ...                 ...   
5007                 False               False   
5010                 False               False   
5013                 False               False   
5016                 False               False   
5019                 False               False   

                                  normed_column  harmonics_considered  \
2     normed_values_normed_weighted_modulations                     2   
5     normed_values_normed_weighted_modulations                     3   
8     normed_values_normed_weighted_modulations                     4   
11    normed_values_normed_weighted_modulations                     5   
14    normed_values_normed_weighted_modulations                     6   
...                                         ...                   ...   
5007             normed_values_only_modulations                    28   
5010             normed_values_only_modulations                    29   
5013             normed_values_only_modulations                    30   
5016             normed_values_only_modulations                    31   
5019             normed_values_only_modulations                    32   

      correlation   p_value  \
2        0.073246  0.812035   
5        0.209963  0.491145   
8        0.188181  0.538112   
11       0.118554  0.699684   
14       0.142702  0.641881   
...           ...       ...   
5007     0.233293  0.443038   
5010     0.215352  0.479825   
5013     0.220942  0.468213   
5016     0.225580  0.458680   
5019     0.230926  0.447811   

                                final_ranking_correlate      compared_with  \
2     [0.2560975609756097, 0.2560975609756097, 0.128...  numbered_rankings   
5     [0.1150793650793649, 0.1150793650793649, 0.086...  numbered_rankings   
8     [0.1479729869271598, 0.1479729869271598, 0.076...  numbered_rankings   
11    [0.2134432237560609, 0.2134432237560609, 0.102...  numbered_rankings   
14    [0.1981854451027551, 0.198185445102755, 0.1182...  numbered_rankings   
...                                                 ...                ...   
5007  [0.825, 0.825, 0.325, 0.0, 0.5, 0.4, 0.4, 0.5,...      ranking_order   
5010  [0.782608695652174, 0.782608695652174, 0.28260...      ranking_order   
5013  [0.7708333333333334, 0.7708333333333334, 0.270...      ranking_order   
5016  [0.78, 0.78, 0.28, 0.0, 0.5, 0.34, 0.34, 0.5, ...      ranking_order   
5019  [0.8333333333333334, 0.8333333333333334, 0.333...      ranking_order   

     cleaned_method_name  
2               Method E  
5               Method E  
8               Method E  
11              Method E  
14              Method E  
...                  ...  
5007            Method A  
5010            Method A  
5013            Method A  
5016            Method A  
5019            Method A  

[1642 rows x 12 columns]

In [32]:
new_df_with_explicit_ratings.to_csv('../data_csvs/ihm_correlation_triads_with_empirical.csv', index=False)

## reading clean csv

In [33]:
new_df_with_explicit_ratings = pd.read_csv('../data_csvs/ihm_correlation_triads_with_empirical.csv')
new_df_with_explicit_ratings

method  r_names_used         distributive  \
0     Experimental_methods     all_ranges  weight_interval_sum   
1     Experimental_methods     all_ranges  weight_interval_sum   
2     Experimental_methods     all_ranges  weight_interval_sum   
3     Experimental_methods     all_ranges  weight_interval_sum   
4     Experimental_methods     all_ranges  weight_interval_sum   
...                     ...           ...                  ...   
1637  Chan's method Vanilla  chan_vanilla                False   
1638  Chan's method Vanilla  chan_vanilla                False   
1639  Chan's method Vanilla  chan_vanilla                False   
1640  Chan's method Vanilla  chan_vanilla                False   
1641  Chan's method Vanilla  chan_vanilla                False   

      weights_on_harmonics  weights_on_regions  \
0                     True                True   
1                     True                True   
2                     True                True   
3                     True                True   
4                     True                True   
...                    ...                 ...   
1637                 False               False   
1638                 False               False   
1639                 False               False   
1640                 False               False   
1641                 False               False   

                                  normed_column  harmonics_considered  \
0     normed_values_normed_weighted_modulations                     2   
1     normed_values_normed_weighted_modulations                     3   
2     normed_values_normed_weighted_modulations                     4   
3     normed_values_normed_weighted_modulations                     5   
4     normed_values_normed_weighted_modulations                     6   
...                                         ...                   ...   
1637             normed_values_only_modulations                    28   
1638             normed_values_only_modulations                    29   
1639             normed_values_only_modulations                    30   
1640             normed_values_only_modulations                    31   
1641             normed_values_only_modulations                    32   

      correlation   p_value  \
0        0.073246  0.812035   
1        0.209963  0.491145   
2        0.188181  0.538112   
3        0.118554  0.699684   
4        0.142702  0.641881   
...           ...       ...   
1637     0.233293  0.443038   
1638     0.215352  0.479825   
1639     0.220942  0.468213   
1640     0.225580  0.458680   
1641     0.230926  0.447811   

                                final_ranking_correlate      compared_with  \
0     [0.2560975609756097, 0.2560975609756097, 0.128...  numbered_rankings   
1     [0.1150793650793649, 0.1150793650793649, 0.086...  numbered_rankings   
2     [0.1479729869271598, 0.1479729869271598, 0.076...  numbered_rankings   
3     [0.2134432237560609, 0.2134432237560609, 0.102...  numbered_rankings   
4     [0.1981854451027551, 0.198185445102755, 0.1182...  numbered_rankings   
...                                                 ...                ...   
1637  [0.825, 0.825, 0.325, 0.0, 0.5, 0.4, 0.4, 0.5,...      ranking_order   
1638  [0.782608695652174, 0.782608695652174, 0.28260...      ranking_order   
1639  [0.7708333333333334, 0.7708333333333334, 0.270...      ranking_order   
1640  [0.78, 0.78, 0.28, 0.0, 0.5, 0.34, 0.34, 0.5, ...      ranking_order   
1641  [0.8333333333333334, 0.8333333333333334, 0.333...      ranking_order   

     cleaned_method_name  
0               Method E  
1               Method E  
2               Method E  
3               Method E  
4               Method E  
...                  ...  
1637            Method A  
1638            Method A  
1639            Method A  
1640            Method A  
1641            Method A  

[1642 rows x 12 columns]

# Graphs

In [34]:
df_to_work_with = pd.read_csv('../data_csvs/clean_ihm_intervals_normalized_tension_scores_correlation.csv')

In [35]:
df_to_work_with

method  r_names_used  distributive  weights_on_harmonics  \
0    Experimental_methods     all_ranges          True                  True   
1    Experimental_methods     all_ranges          True                  True   
2    Experimental_methods     all_ranges          True                  True   
3    Experimental_methods     all_ranges          True                  True   
4    Experimental_methods     all_ranges          True                  True   
..                     ...           ...           ...                   ...   
274  Chan's method Vanilla  chan_vanilla          True                 False   
275  Chan's method Vanilla  chan_vanilla          True                 False   
276  Chan's method Vanilla  chan_vanilla          True                 False   
277  Chan's method Vanilla  chan_vanilla          True                 False   
278  Chan's method Vanilla  chan_vanilla          True                 False   

     weights_on_regions                              normed_column  \
0                  True  normed_values_normed_weighted_modulations   
1                  True  normed_values_normed_weighted_modulations   
2                  True  normed_values_normed_weighted_modulations   
3                  True  normed_values_normed_weighted_modulations   
4                  True  normed_values_normed_weighted_modulations   
..                  ...                                        ...   
274               False             normed_values_only_modulations   
275               False             normed_values_only_modulations   
276               False             normed_values_only_modulations   
277               False             normed_values_only_modulations   
278               False             normed_values_only_modulations   

     harmonics_considered  correlation   p_value  \
0                       2     0.887170  0.000052   
1                       3     0.903150  0.000023   
2                       4     0.916195  0.000011   
3                       5     0.877249  0.000082   
4                       6     0.875810  0.000087   
..                    ...          ...       ...   
274                    28     0.486403  0.091901   
275                    29     0.485307  0.092744   
276                    30     0.480084  0.096840   
277                    31     0.446446  0.126195   
278                    32     0.412435  0.161363   

                               final_ranking_correlate cleaned_method_name  
0    [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314,...            Method E  
1    [0.0, 0.0, 0.0, 0.125, 0.21875, 0.441964285714...            Method E  
2    [0.0, 0.0, 0.06849315068493153, 0.155251141552...            Method E  
3    [0.0, 0.01986123209400906, 0.11665631331368023...            Method E  
4    [0.02816911025807649, 0.0, 0.1413188191357587,...            Method E  
..                                                 ...                 ...  
274  [0.5172413793103449, 0.0, 0.22413793103448276,...            Method A  
275  [0.5, 0.0, 0.20967741935483872, 0.338709677419...            Method A  
276  [0.49230769230769234, 0.0, 0.2153846153846154,...            Method A  
277  [0.5151515151515151, 0.0, 0.21212121212121213,...            Method A  
278  [0.5606060606060606, 0.0, 0.19696969696969696,...            Method A  

[279 rows x 11 columns]

In [36]:
### joining chan_vanilla with ranges

# Get vanilla data and other r_names_used values
vanilla_df = df_to_work_with[df_to_work_with['r_names_used'] == 'chan_vanilla'].copy()
other_r_names = df_to_work_with[df_to_work_with['r_names_used'] != 'chan_vanilla']['r_names_used'].unique()

# Create duplicated data for each other r_names_used category
duplicated_data = []
for r_name in other_r_names:
    temp_df = vanilla_df.copy()
    temp_df['r_names_used'] = r_name
    duplicated_data.append(temp_df)


# remove chan_vanilla from original dataframe
df_to_work_with = df_to_work_with[df_to_work_with['r_names_used'] != 'chan_vanilla']
# Combine everything

df_with_duplicated_vanilla_intervals = pd.concat([df_to_work_with] + duplicated_data, ignore_index=True)
df_with_duplicated_vanilla_intervals['exp_with'] = "Intervals"

In [37]:
df_with_duplicated_vanilla_intervals


method    r_names_used  distributive  \
0    Experimental_methods       all_ranges          True   
1    Experimental_methods       all_ranges          True   
2    Experimental_methods       all_ranges          True   
3    Experimental_methods       all_ranges          True   
4    Experimental_methods       all_ranges          True   
..                     ...             ...           ...   
305  Chan's method Vanilla  start_from_0.5          True   
306  Chan's method Vanilla  start_from_0.5          True   
307  Chan's method Vanilla  start_from_0.5          True   
308  Chan's method Vanilla  start_from_0.5          True   
309  Chan's method Vanilla  start_from_0.5          True   

     weights_on_harmonics  weights_on_regions  \
0                    True                True   
1                    True                True   
2                    True                True   
3                    True                True   
4                    True                True   
..                    ...                 ...   
305                 False               False   
306                 False               False   
307                 False               False   
308                 False               False   
309                 False               False   

                                 normed_column  harmonics_considered  \
0    normed_values_normed_weighted_modulations                     2   
1    normed_values_normed_weighted_modulations                     3   
2    normed_values_normed_weighted_modulations                     4   
3    normed_values_normed_weighted_modulations                     5   
4    normed_values_normed_weighted_modulations                     6   
..                                         ...                   ...   
305             normed_values_only_modulations                    28   
306             normed_values_only_modulations                    29   
307             normed_values_only_modulations                    30   
308             normed_values_only_modulations                    31   
309             normed_values_only_modulations                    32   

     correlation   p_value                            final_ranking_correlate  \
0       0.887170  0.000052  [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314,...   
1       0.903150  0.000023  [0.0, 0.0, 0.0, 0.125, 0.21875, 0.441964285714...   
2       0.916195  0.000011  [0.0, 0.0, 0.06849315068493153, 0.155251141552...   
3       0.877249  0.000082  [0.0, 0.01986123209400906, 0.11665631331368023...   
4       0.875810  0.000087  [0.02816911025807649, 0.0, 0.1413188191357587,...   
..           ...       ...                                                ...   
305     0.486403  0.091901  [0.5172413793103449, 0.0, 0.22413793103448276,...   
306     0.485307  0.092744  [0.5, 0.0, 0.20967741935483872, 0.338709677419...   
307     0.480084  0.096840  [0.49230769230769234, 0.0, 0.2153846153846154,...   
308     0.446446  0.126195  [0.5151515151515151, 0.0, 0.21212121212121213,...   
309     0.412435  0.161363  [0.5606060606060606, 0.0, 0.19696969696969696,...   

    cleaned_method_name   exp_with  
0              Method E  Intervals  
1              Method E  Intervals  
2              Method E  Intervals  
3              Method E  Intervals  
4              Method E  Intervals  
..                  ...        ...  
305            Method A  Intervals  
306            Method A  Intervals  
307            Method A  Intervals  
308            Method A  Intervals  
309            Method A  Intervals  

[310 rows x 12 columns]

In [38]:
df_to_work_with = pd.read_csv('../data_csvs/ihm_correlation_triads_with_empirical.csv')
df_to_work_with

method  r_names_used         distributive  \
0     Experimental_methods     all_ranges  weight_interval_sum   
1     Experimental_methods     all_ranges  weight_interval_sum   
2     Experimental_methods     all_ranges  weight_interval_sum   
3     Experimental_methods     all_ranges  weight_interval_sum   
4     Experimental_methods     all_ranges  weight_interval_sum   
...                     ...           ...                  ...   
1637  Chan's method Vanilla  chan_vanilla                False   
1638  Chan's method Vanilla  chan_vanilla                False   
1639  Chan's method Vanilla  chan_vanilla                False   
1640  Chan's method Vanilla  chan_vanilla                False   
1641  Chan's method Vanilla  chan_vanilla                False   

      weights_on_harmonics  weights_on_regions  \
0                     True                True   
1                     True                True   
2                     True                True   
3                     True                True   
4                     True                True   
...                    ...                 ...   
1637                 False               False   
1638                 False               False   
1639                 False               False   
1640                 False               False   
1641                 False               False   

                                  normed_column  harmonics_considered  \
0     normed_values_normed_weighted_modulations                     2   
1     normed_values_normed_weighted_modulations                     3   
2     normed_values_normed_weighted_modulations                     4   
3     normed_values_normed_weighted_modulations                     5   
4     normed_values_normed_weighted_modulations                     6   
...                                         ...                   ...   
1637             normed_values_only_modulations                    28   
1638             normed_values_only_modulations                    29   
1639             normed_values_only_modulations                    30   
1640             normed_values_only_modulations                    31   
1641             normed_values_only_modulations                    32   

      correlation   p_value  \
0        0.073246  0.812035   
1        0.209963  0.491145   
2        0.188181  0.538112   
3        0.118554  0.699684   
4        0.142702  0.641881   
...           ...       ...   
1637     0.233293  0.443038   
1638     0.215352  0.479825   
1639     0.220942  0.468213   
1640     0.225580  0.458680   
1641     0.230926  0.447811   

                                final_ranking_correlate      compared_with  \
0     [0.2560975609756097, 0.2560975609756097, 0.128...  numbered_rankings   
1     [0.1150793650793649, 0.1150793650793649, 0.086...  numbered_rankings   
2     [0.1479729869271598, 0.1479729869271598, 0.076...  numbered_rankings   
3     [0.2134432237560609, 0.2134432237560609, 0.102...  numbered_rankings   
4     [0.1981854451027551, 0.198185445102755, 0.1182...  numbered_rankings   
...                                                 ...                ...   
1637  [0.825, 0.825, 0.325, 0.0, 0.5, 0.4, 0.4, 0.5,...      ranking_order   
1638  [0.782608695652174, 0.782608695652174, 0.28260...      ranking_order   
1639  [0.7708333333333334, 0.7708333333333334, 0.270...      ranking_order   
1640  [0.78, 0.78, 0.28, 0.0, 0.5, 0.34, 0.34, 0.5, ...      ranking_order   
1641  [0.8333333333333334, 0.8333333333333334, 0.333...      ranking_order   

     cleaned_method_name  
0               Method E  
1               Method E  
2               Method E  
3               Method E  
4               Method E  
...                  ...  
1637            Method A  
1638            Method A  
1639            Method A  
1640            Method A  
1641            Method A  

[1642 rows x 12 columns]

In [39]:
### joining with chan_vanilla ranges
vanilla_df = df_to_work_with[df_to_work_with['r_names_used'] == 'chan_vanilla'].copy()
vanilla_df

method  r_names_used         distributive  \
728   Chan's method Vanilla  chan_vanilla  weight_interval_sum   
729   Chan's method Vanilla  chan_vanilla  weight_interval_sum   
730   Chan's method Vanilla  chan_vanilla  weight_interval_sum   
731   Chan's method Vanilla  chan_vanilla  weight_interval_sum   
732   Chan's method Vanilla  chan_vanilla  weight_interval_sum   
...                     ...           ...                  ...   
1637  Chan's method Vanilla  chan_vanilla                False   
1638  Chan's method Vanilla  chan_vanilla                False   
1639  Chan's method Vanilla  chan_vanilla                False   
1640  Chan's method Vanilla  chan_vanilla                False   
1641  Chan's method Vanilla  chan_vanilla                False   

      weights_on_harmonics  weights_on_regions  \
728                  False               False   
729                  False               False   
730                  False               False   
731                  False               False   
732                  False               False   
...                    ...                 ...   
1637                 False               False   
1638                 False               False   
1639                 False               False   
1640                 False               False   
1641                 False               False   

                       normed_column  harmonics_considered  correlation  \
728   normed_values_only_modulations                     2    -0.141078   
729   normed_values_only_modulations                     3     0.102122   
730   normed_values_only_modulations                     4     0.083453   
731   normed_values_only_modulations                     5     0.018997   
732   normed_values_only_modulations                     6     0.103463   
...                              ...                   ...          ...   
1637  normed_values_only_modulations                    28     0.233293   
1638  normed_values_only_modulations                    29     0.215352   
1639  normed_values_only_modulations                    30     0.220942   
1640  normed_values_only_modulations                    31     0.225580   
1641  normed_values_only_modulations                    32     0.230926   

       p_value                            final_ranking_correlate  \
728   0.645717  [0.5, 0.5, 0.25, 0.25, 0.5, 0.5, 0.5, 0.5, 0.7...   
729   0.739907  [0.25, 0.25, 0.25, 0.25, 0.5, 0.25, 0.25, 0.5,...   
730   0.786356  [0.4285714285714285, 0.4285714285714285, 0.142...   
731   0.950882  [0.4545454545454545, 0.4545454545454545, 0.090...   
732   0.736601  [0.2727272727272727, 0.2727272727272727, 0.181...   
...        ...                                                ...   
1637  0.443038  [0.825, 0.825, 0.325, 0.0, 0.5, 0.4, 0.4, 0.5,...   
1638  0.479825  [0.782608695652174, 0.782608695652174, 0.28260...   
1639  0.468213  [0.7708333333333334, 0.7708333333333334, 0.270...   
1640  0.458680  [0.78, 0.78, 0.28, 0.0, 0.5, 0.34, 0.34, 0.5, ...   
1641  0.447811  [0.8333333333333334, 0.8333333333333334, 0.333...   

          compared_with cleaned_method_name  
728   numbered_rankings            Method A  
729   numbered_rankings            Method A  
730   numbered_rankings            Method A  
731   numbered_rankings            Method A  
732   numbered_rankings            Method A  
...                 ...                 ...  
1637      ranking_order            Method A  
1638      ranking_order            Method A  
1639      ranking_order            Method A  
1640      ranking_order            Method A  
1641      ranking_order            Method A  

[186 rows x 12 columns]

In [40]:
other_r_names = df_to_work_with[df_to_work_with['r_names_used'] != 'chan_vanilla']['r_names_used'].unique()

# Create duplicated data for each other r_names_used category
duplicated_data = []
for r_name in other_r_names:
    temp_df = vanilla_df.copy()
    temp_df['r_names_used'] = r_name
    duplicated_data.append(temp_df)
# remove chan_vanilla from original dataframe
df_to_work_with = df_to_work_with[df_to_work_with['r_names_used'] != 'chan_vanilla']
# Combine everything
df_with_duplicated_vanilla_triads = pd.concat([df_to_work_with] + duplicated_data, ignore_index=True)
df_with_duplicated_vanilla_triads['exp_with'] = "Triads"

In [41]:
df_with_duplicated_vanilla_triads

method    r_names_used         distributive  \
0     Experimental_methods       all_ranges  weight_interval_sum   
1     Experimental_methods       all_ranges  weight_interval_sum   
2     Experimental_methods       all_ranges  weight_interval_sum   
3     Experimental_methods       all_ranges  weight_interval_sum   
4     Experimental_methods       all_ranges  weight_interval_sum   
...                     ...             ...                  ...   
1823  Chan's method Vanilla  start_from_0.5                False   
1824  Chan's method Vanilla  start_from_0.5                False   
1825  Chan's method Vanilla  start_from_0.5                False   
1826  Chan's method Vanilla  start_from_0.5                False   
1827  Chan's method Vanilla  start_from_0.5                False   

      weights_on_harmonics  weights_on_regions  \
0                     True                True   
1                     True                True   
2                     True                True   
3                     True                True   
4                     True                True   
...                    ...                 ...   
1823                 False               False   
1824                 False               False   
1825                 False               False   
1826                 False               False   
1827                 False               False   

                                  normed_column  harmonics_considered  \
0     normed_values_normed_weighted_modulations                     2   
1     normed_values_normed_weighted_modulations                     3   
2     normed_values_normed_weighted_modulations                     4   
3     normed_values_normed_weighted_modulations                     5   
4     normed_values_normed_weighted_modulations                     6   
...                                         ...                   ...   
1823             normed_values_only_modulations                    28   
1824             normed_values_only_modulations                    29   
1825             normed_values_only_modulations                    30   
1826             normed_values_only_modulations                    31   
1827             normed_values_only_modulations                    32   

      correlation   p_value  \
0        0.073246  0.812035   
1        0.209963  0.491145   
2        0.188181  0.538112   
3        0.118554  0.699684   
4        0.142702  0.641881   
...           ...       ...   
1823     0.233293  0.443038   
1824     0.215352  0.479825   
1825     0.220942  0.468213   
1826     0.225580  0.458680   
1827     0.230926  0.447811   

                                final_ranking_correlate      compared_with  \
0     [0.2560975609756097, 0.2560975609756097, 0.128...  numbered_rankings   
1     [0.1150793650793649, 0.1150793650793649, 0.086...  numbered_rankings   
2     [0.1479729869271598, 0.1479729869271598, 0.076...  numbered_rankings   
3     [0.2134432237560609, 0.2134432237560609, 0.102...  numbered_rankings   
4     [0.1981854451027551, 0.198185445102755, 0.1182...  numbered_rankings   
...                                                 ...                ...   
1823  [0.825, 0.825, 0.325, 0.0, 0.5, 0.4, 0.4, 0.5,...      ranking_order   
1824  [0.782608695652174, 0.782608695652174, 0.28260...      ranking_order   
1825  [0.7708333333333334, 0.7708333333333334, 0.270...      ranking_order   
1826  [0.78, 0.78, 0.28, 0.0, 0.5, 0.34, 0.34, 0.5, ...      ranking_order   
1827  [0.8333333333333334, 0.8333333333333334, 0.333...      ranking_order   

     cleaned_method_name exp_with  
0               Method E   Triads  
1               Method E   Triads  
2               Method E   Triads  
3               Method E   Triads  
4               Method E   Triads  
...                  ...      ...  
1823            Method A   Triads  
1824            Method A   Triads  
1825            Method A   Triads  
1826            Method A   Triads  
1827            Meth

## Joining both to have IHM experiments all together


In [42]:
df = pd.concat([df_with_duplicated_vanilla_intervals, df_with_duplicated_vanilla_triads], ignore_index=True)
df.to_csv('../data_csvs/ihm_combined_intervals_and_triads.csv', index=False)

In [43]:
df = pd.read_csv('../data_csvs/ihm_combined_intervals_and_triads.csv')
## creating new row for exp_with and compared_with for a final column called ground_truth_type
for i, row in df.iterrows():
    if row['exp_with'] == 'Intervals':
        df.at[i, 'ground_truth_type'] = 'Interval Ranking Order'
    elif row['exp_with'] == 'Triads':
        if row['compared_with'] == 'numbered_rankings':
            df.at[i, 'ground_truth_type'] = 'Triad Explicit Ratings'
        else:
            df.at[i, 'ground_truth_type'] = 'Triad Ranking Order'
    if row['r_names_used'] =='all_ranges':
        df.at[i,'r_names_used']='All r_bounds Considered'
    elif row['r_names_used']=='start_from_0.5':
        df.at[i,'r_names_used']='Starting from r_lower==0.25'



## IHM boxplot

In [44]:
interval_df = df[df['exp_with']=='Intervals']  

chart = alt.Chart(interval_df).encode(
    x=alt.X('cleaned_method_name:N', title='Different Methods' ,axis=alt.Axis(labelAngle=-45)),
    y=alt.Y('correlation:Q', title='Correlation with Interval Ranking'),
    # facet=alt.Facet(title=None)
)
chart.mark_boxplot().properties(width=200,height=200,).facet(column=alt.Column('r_names_used:N',title="Different r_bounds considered")).properties(
    title='Interharmonic Method Correlations with Empirical Interval Rankings').configure_title(anchor='end')


alt.FacetChart(...)

## intervals line chart

In [47]:



chart.mark_line().encode(
    x=alt.X('harmonics_considered:Q'),
    y=alt.Y('correlation:Q'),
    color=alt.Color('cleaned_method_name:N')
).facet(row='r_names_used:N')

alt.FacetChart(...)

## Interharmonic boxplot distributive

## Boxplot, distributive vs r_range

In [45]:
triads_df = df[df['exp_with']=='Triads']
num_ranked = triads_df[triads_df['compared_with']=='numbered_rankings']
ranking_only = triads_df[triads_df['compared_with']=='ranking_order']
num_ranked_chart= alt.Chart(num_ranked).mark_boxplot().encode(
    x=alt.X('cleaned_method_name:N', title='Different Methods', axis=alt.Axis(labelAngle=-45)),
    y=alt.Y('correlation:Q',title=None),
    color=alt.Color('distributive:N', scale=alt.Scale(scheme='dark2'),legend=alt.Legend(title="Distributive Computation"))   
).properties(width=125,height=150).facet(row=alt.Row('r_names_used:N',title='Correlation computed on differnt r_bounds'), column=alt.Column('distributive:N',title=None,header=alt.Header(title='Numbered Explicit Ratings',labels=False)))
ranking_only_chart= alt.Chart(ranking_only).mark_boxplot().encode(
    x=alt.X('cleaned_method_name:N', title='Different Methods', axis=alt.Axis(labelAngle=-45)),
    y=alt.Y('correlation:Q',title=None),
    color=alt.Color('distributive:N', scale=alt.Scale(scheme='dark2'),legend=alt.Legend(title="Distributive Computation"))   
).properties(width=125,height=150).facet(row=alt.Row('r_names_used:N',title=None,header=None), column=alt.Column('distributive:N',title=None,header=alt.Header(title='Ranking Order Only',labels=False)))


In [46]:
(num_ranked_chart | ranking_only_chart).resolve_scale(y='shared').properties(title='Interharmonic Methods Correlations Comparison for Triads using Distributive Methods').configure_title(anchor='middle').configure_legend(orient='bottom',titleAnchor='middle')

alt.HConcatChart(...)

## mixing graphs faceting

### Corr line chart

In [57]:
df[df['cleaned_method_name']=='Method A']

method                 r_names_used distributive  \
248   Chan's method Vanilla      All r_bounds Considered         True   
249   Chan's method Vanilla      All r_bounds Considered         True   
250   Chan's method Vanilla      All r_bounds Considered         True   
251   Chan's method Vanilla      All r_bounds Considered         True   
252   Chan's method Vanilla      All r_bounds Considered         True   
...                     ...                          ...          ...   
2133  Chan's method Vanilla  Starting from r_lower==0.25        False   
2134  Chan's method Vanilla  Starting from r_lower==0.25        False   
2135  Chan's method Vanilla  Starting from r_lower==0.25        False   
2136  Chan's method Vanilla  Starting from r_lower==0.25        False   
2137  Chan's method Vanilla  Starting from r_lower==0.25        False   

      weights_on_harmonics  weights_on_regions  \
248                  False               False   
249                  False               False   
250                  False               False   
251                  False               False   
252                  False               False   
...                    ...                 ...   
2133                 False               False   
2134                 False               False   
2135                 False               False   
2136                 False               False   
2137                 False               False   

                       normed_column  harmonics_considered  correlation  \
248   normed_values_only_modulations                     2     0.725908   
249   normed_values_only_modulations                     3     0.744513   
250   normed_values_only_modulations                     4     0.751033   
251   normed_values_only_modulations                     5     0.803837   
252   normed_values_only_modulations                     6     0.848788   
...                              ...                   ...          ...   
2133  normed_values_only_modulations                    28     0.233293   
2134  normed_values_only_modulations                    29     0.215352   
2135  normed_values_only_modulations                    30     0.220942   
2136  normed_values_only_modulations                    31     0.225580   
2137  normed_values_only_modulations                    32     0.230926   

       p_value                            final_ranking_correlate  \
248   0.004967  [0.0, 0.0, 0.0, 0.0, 0.0, 0.5, 0.0, 1.0, 0.0, ...   
249   0.003510  [0.0, 0.0, 0.0, 0.3333333333333333, 0.33333333...   
250   0.003087  [0.0, 0.0, 0.2, 0.2, 0.4, 0.6, 0.4, 1.0, 0.4, ...   
251   0.000929  [0.0, 0.0, 0.2857142857142857, 0.1428571428571...   
252   0.000243  [0.0, 0.0, 0.25, 0.375, 0.375, 0.625, 0.375, 0...   
...        ...                                                ...   
2133  0.443038  [0.825, 0.825, 0.325, 0.0, 0.5, 0.4, 0.4, 0.5,...   
2134  0.479825  [0.782608695652174, 0.782608695652174, 0.28260...   
2135  0.468213  [0.7708333333333334, 0.7708333333333334, 0.270...   
2136  0.458680  [0.78, 0.78, 0.28, 0.0, 0.5, 0.34, 0.34, 0.5, ...   
2137  0.447811  [0.8333333333333334, 0.8333333333333334, 0.333...   

     cleaned_method_name   exp_with  compared_with       ground_truth_type  
248             Method A  Intervals            NaN  Interval Ranking Order  
249             Method A  Intervals            NaN  Interval Ranking Order  
250             Method A  Intervals            NaN  Interval Ranking Order  
251             Method A  Intervals            NaN  Interval Ranking Order  
252             Method A  Intervals            NaN  Interval Ranking Order  
...                  ...        ...            ...                     ...  
2133            Method A     Triads  ranking_order     Triad Ranking Order  
2134            Method A     Triads  ranking_order     Triad Ranking Order  
2135            Method A     Triads  ranking_order     Triad Ranking Order  
2136            Method A     Triads  rankin

In [ ]:
df_to_use = df[df['distributive']!=False]
df_dist = df_to_use[df_to_use['distributive']=='all_modulations_weight']

line_chart = alt.Chart(df_dist).mark_line().encode(
    x=alt.X('harmonics_considered:Q',title='Harmonics Considered'),
    y=alt.Y('correlation:Q', title=None),
    color=alt.Color('cleaned_method_name:N', legend=alt.Legend(title='Different Methods'))
).properties(height=200,width=200).facet(
    column=alt.Column('ground_truth_type:N',
                      header=alt.Header(title='Type of Ground Truth Compared To',labelFontWeight='bold',titleFontSize=12)), 
    row=alt.Row('r_names_used:N',
                header=alt.Header(title='Correlation considering different r_bounds')), align='all')
line_chart.properties(title="Correlation Chart for each Method Varying the Harmonics").configure_legend(orient='bottom').configure_title(anchor='middle',fontSize=16)

alt.FacetChart(...)

## Case by case line chart

In [21]:
## ground truth for black line
normed_ranking = [1,2,3,4,5,6,7,8,9,10,11,12,13]
normalized_values = [(x - min(normed_ranking)) / (max(normed_ranking) - min(normed_ranking)) for x in normed_ranking]
df_gt = pd.DataFrame({
    'normalized_value':normalized_values,
    'chord_label':empirical_ranking_intervals
})
df_gt

normalized_value chord_label
0           0.000000           U
1           0.083333          8v
2           0.166667          P5
3           0.250000          P4
4           0.333333          M3
5           0.416667          M6
6           0.500000          m6
7           0.583333          m3
8           0.666667          TT
9           0.750000          m7
10          0.833333          M2
11          0.916667          M7
12          1.000000          m2

In [22]:
intervals = df_to_use[df_to_use['exp_with']=='Intervals']
intervals

method                 r_names_used  distributive  \
0    Experimental_methods       All r_bounds Considered          True   
1    Experimental_methods       All r_bounds Considered          True   
2    Experimental_methods       All r_bounds Considered          True   
3    Experimental_methods       All r_bounds Considered          True   
4    Experimental_methods       All r_bounds Considered          True   
..                     ...                          ...           ...   
305  Chan's method Vanilla  Starting from r_lower==0.25          True   
306  Chan's method Vanilla  Starting from r_lower==0.25          True   
307  Chan's method Vanilla  Starting from r_lower==0.25          True   
308  Chan's method Vanilla  Starting from r_lower==0.25          True   
309  Chan's method Vanilla  Starting from r_lower==0.25          True   

     weights_on_harmonics  weights_on_regions  \
0                    True                True   
1                    True                True   
2                    True                True   
3                    True                True   
4                    True                True   
..                    ...                 ...   
305                 False               False   
306                 False               False   
307                 False               False   
308                 False               False   
309                 False               False   

                                 normed_column  harmonics_considered  \
0    normed_values_normed_weighted_modulations                     2   
1    normed_values_normed_weighted_modulations                     3   
2    normed_values_normed_weighted_modulations                     4   
3    normed_values_normed_weighted_modulations                     5   
4    normed_values_normed_weighted_modulations                     6   
..                                         ...                   ...   
305             normed_values_only_modulations                    28   
306             normed_values_only_modulations                    29   
307             normed_values_only_modulations                    30   
308             normed_values_only_modulations                    31   
309             normed_values_only_modulations                    32   

     correlation   p_value                            final_ranking_correlate  \
0       0.887170  0.000052  [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314,...   
1       0.903150  0.000023  [0.0, 0.0, 0.0, 0.125, 0.21875, 0.441964285714...   
2       0.916195  0.000011  [0.0, 0.0, 0.06849315068493153, 0.155251141552...   
3       0.877249  0.000082  [0.0, 0.01986123209400906, 0.11665631331368023...   
4       0.875810  0.000087  [0.02816911025807649, 0.0, 0.1413188191357587,...   
..           ...       ...                                                ...   
305     0.486403  0.091901  [0.5172413793103449, 0.0, 0.22413793103448276,...   
306     0.485307  0.092744  [0.5, 0.0, 0.20967741935483872, 0.338709677419...   
307     0.480084  0.096840  [0.49230769230769234, 0.0, 0.2153846153846154,...   
308     0.446446  0.126195  [0.5151515151515151, 0.0, 0.21212121212121213,...   
309     0.412435  0.161363  [0.5606060606060606, 0.0, 0.19696969696969696,...   

    cleaned_method_name   exp_with compared_with       ground_truth_type  
0              Method E  Intervals           NaN  Interval Ranking Order  
1              Method E  Intervals           NaN  Interval Ranking Order  
2              Method E  Intervals           NaN  Interval Ranking Order  
3              Method E  Intervals           NaN  Interval Ranking Order  
4              Method E  Intervals           NaN  Interval Ranking Order  
..                  ...        ...           ...                     ...  
305            Method A  Intervals           NaN  Interval Ranking Order  
306            Method A  Intervals           NaN  Interval Ranking Order  
307            Method A  Intervals       

In [23]:

chord_label_df_ranking_intervals = ihm.convert_correlation_df_to_a_line_chart_df(intervals, empirical_ranking_names=empirical_ranking_intervals, column_to_convert='final_ranking_correlate', group_by_methods_array=['cleaned_method_name','exp_with','r_names_used','harmonics_considered','ground_truth_type'])
chord_label_df_ranking_intervals[chord_label_df_ranking_intervals['cleaned_method_name']=='Method B']

Normalized values for each rank: [0.0, 0.0, 0.0, 0.0, 0.0, 0.22580645161290314, 0.0, 0.45161290322580633, 0.8602150537634407, 1.0, 0.7956989247311826, 1.0, 0.7956989247311826]
Normalized values for each rank: [0.0, 0.0, 0.0, 0.125, 0.21875, 0.44196428571428586, 0.2125, 0.6124999999999999, 1.0, 0.9723214285714288, 0.8187499999999999, 0.8598214285714285, 0.7721590909090909]
Normalized values for each rank: [0.0, 0.0, 0.06849315068493153, 0.1552511415525114, 0.228310502283105, 0.391906786332861, 0.2031963470319635, 0.5871020203915683, 1.0, 0.8765548732483076, 0.7938950397197725, 0.8825381829633131, 0.8022562449637392]
Normalized values for each rank: [0.0, 0.01986123209400906, 0.11665631331368023, 0.18318264265859469, 0.1518729408417652, 0.2858140629406891, 0.15276409493383497, 0.5304096959710197, 1.0, 0.8396906151489979, 0.7748191386930585, 0.7308088997576209, 0.7181934386814437]
Normalized values for each rank: [0.02816911025807649, 0.0, 0.1413188191357587, 0.216366158113731, 0.21194082

chord_label  normalized_value cleaned_method_name   exp_with  \
1209           U          1.000000            Method B  Intervals   
1210          8v          0.000000            Method B  Intervals   
1211          P5          1.000000            Method B  Intervals   
1212          P4          1.000000            Method B  Intervals   
1213          M3          1.000000            Method B  Intervals   
...          ...               ...                 ...        ...   
3219          TT          0.790698            Method B  Intervals   
3220          m7          0.395349            Method B  Intervals   
3221          M2          0.965116            Method B  Intervals   
3222          M7          0.279070            Method B  Intervals   
3223          m2          1.000000            Method B  Intervals   

                     r_names_used  harmonics_considered  \
1209      All r_bounds Considered                     2   
1210      All r_bounds Considered                     2   
1211      All r_bounds Considered                     2   
1212      All r_bounds Considered                     2   
1213      All r_bounds Considered                     2   
...                           ...                   ...   
3219  Starting from r_lower==0.25                    32   
3220  Starting from r_lower==0.25                    32   
3221  Starting from r_lower==0.25                    32   
3222  Starting from r_lower==0.25                    32   
3223  Starting from r_lower==0.25                    32   

           ground_truth_type  
1209  Interval Ranking Order  
1210  Interval Ranking Order  
1211  Interval Ranking Order  
1212  Interval Ranking Order  
1213  Interval Ranking Order  
...                      ...  
3219  Interval Ranking Order  
3220  Interval Ranking Order  
3221  Interval Ranking Order  
3222  Interval Ranking Order  
3223  Interval Ranking Order  

[806 rows x 7 columns]

13 intervalos * 5 metodos* 2 ranges * 31 armonicos

In [24]:
triads_explicit = df_to_use[df_to_use['ground_truth_type']=='Triad Explicit Ratings']
triads_explicit

method                 r_names_used  distributive  \
310   Experimental_methods       All r_bounds Considered          True   
311   Experimental_methods       All r_bounds Considered          True   
312   Experimental_methods       All r_bounds Considered          True   
313   Experimental_methods       All r_bounds Considered          True   
314   Experimental_methods       All r_bounds Considered          True   
...                     ...                          ...           ...   
1420  Chan's method Vanilla  Starting from r_lower==0.25          True   
1421  Chan's method Vanilla  Starting from r_lower==0.25          True   
1422  Chan's method Vanilla  Starting from r_lower==0.25          True   
1423  Chan's method Vanilla  Starting from r_lower==0.25          True   
1424  Chan's method Vanilla  Starting from r_lower==0.25          True   

      weights_on_harmonics  weights_on_regions  \
310                   True                True   
311                   True                True   
312                   True                True   
313                   True                True   
314                   True                True   
...                    ...                 ...   
1420                 False               False   
1421                 False               False   
1422                 False               False   
1423                 False               False   
1424                 False               False   

                                  normed_column  harmonics_considered  \
310   normed_values_normed_weighted_modulations                     2   
311   normed_values_normed_weighted_modulations                     3   
312   normed_values_normed_weighted_modulations                     4   
313   normed_values_normed_weighted_modulations                     5   
314   normed_values_normed_weighted_modulations                     6   
...                                         ...                   ...   
1420             normed_values_only_modulations                    28   
1421             normed_values_only_modulations                    29   
1422             normed_values_only_modulations                    30   
1423             normed_values_only_modulations                    31   
1424             normed_values_only_modulations                    32   

      correlation   p_value  \
310      0.073246  0.812035   
311      0.209963  0.491145   
312      0.188181  0.538112   
313      0.118554  0.699684   
314      0.142702  0.641881   
...           ...       ...   
1420     0.274826  0.363493   
1421     0.220948  0.468201   
1422     0.228718  0.452286   
1423     0.213675  0.483335   
1424     0.238660  0.432310   

                                final_ranking_correlate cleaned_method_name  \
310   [0.2560975609756097, 0.2560975609756097, 0.128...            Method E   
311   [0.1150793650793649, 0.1150793650793649, 0.086...            Method E   
312   [0.1479729869271598, 0.1479729869271598, 0.076...            Method E   
313   [0.2134432237560611, 0.2134432237560609, 0.102...            Method E   
314   [0.1981854451027549, 0.1981854451027549, 0.118...            Method E   
...                                                 ...                 ...   
1420  [0.603448275862069, 0.603448275862069, 0.31034...            Method A   
1421  [0.59375, 0.59375, 0.28125, 0.0, 0.515625, 0.2...            Method A   
1422  [0.5882352941176471, 0.5882352941176471, 0.294...            Method A   
1423  [0.6027397260273972, 0.6027397260273972, 0.287...            Method A   
1424  [0.6455696202531646, 0.6455696202531646, 0.329...            Method A   

     exp_with      compared_with       ground_truth_type  
310    Triads  numbered_rankings  Triad Explicit Ratings  
311    Triads  numbered_rankings  Triad Explicit Ratings  
312    Triads  numbered_rankings  Triad Explicit Ratings  
313    Triads  numbered_rankings  Triad Explicit Ratings  
314    Triads  numbered_rankings  Tri

In [25]:
corr_df_ranking_triads = ihm.convert_correlation_df_to_a_line_chart_df(triads_explicit, empirical_ranking_names=empirical_ranking_triads, column_to_convert='final_ranking_correlate', group_by_methods_array=['cleaned_method_name','exp_with','r_names_used','harmonics_considered','ground_truth_type'])
corr_df_ranking_triads

Normalized values for each rank: [0.2560975609756097, 0.2560975609756097, 0.1280487804878048, 0.5670731707317074, 0.2560975609756097, 0.4512195121951219, 0.4512195121951219, 0.2560975609756097, 0.8719512195121949, 0.1280487804878048, 0.8719512195121949, 1.0, 0.0]
Normalized values for each rank: [0.1150793650793649, 0.1150793650793649, 0.0861678004535148, 0.3633786848072563, 0.1904761904761904, 0.1865079365079363, 0.1865079365079363, 0.1904761904761904, 0.8917233560090703, 0.0861678004535148, 0.8917233560090703, 1.0, 0.0]
Normalized values for each rank: [0.1479729869271598, 0.1479729869271598, 0.0763682614197744, 0.3481540141104351, 0.1886784659548544, 0.2362817785671506, 0.2362817785671506, 0.1886784659548544, 0.8711060817869701, 0.0763682614197744, 0.8711060817869705, 1.0, 0.0]
Normalized values for each rank: [0.2134432237560611, 0.2134432237560609, 0.1024488594617024, 0.4672078320360239, 0.2554659674942698, 0.3853047997744684, 0.3853047997744684, 0.2554659674942696, 0.847538367166

chord_label  normalized_value cleaned_method_name exp_with  \
0             CM          0.256098            Method E   Triads   
1             Cm          0.256098            Method E   Triads   
2          FM2nd          0.128049            Method E   Triads   
3       Fsus42nd          0.567073            Method E   Triads   
4         G#M1st          0.256098            Method E   Triads   
...          ...               ...                 ...      ...   
4025     Adim1st          0.594937            Method A   Triads   
4026       Am1st          0.329114            Method A   Triads   
4027    F#dim2nd          0.594937            Method A   Triads   
4028        Cdim          1.000000            Method A   Triads   
4029        CAug          0.645570            Method A   Triads   

                     r_names_used  harmonics_considered  \
0         All r_bounds Considered                     2   
1         All r_bounds Considered                     2   
2         All r_bounds Considered                     2   
3         All r_bounds Considered                     2   
4         All r_bounds Considered                     2   
...                           ...                   ...   
4025  Starting from r_lower==0.25                    32   
4026  Starting from r_lower==0.25                    32   
4027  Starting from r_lower==0.25                    32   
4028  Starting from r_lower==0.25                    32   
4029  Starting from r_lower==0.25                    32   

           ground_truth_type  
0     Triad Explicit Ratings  
1     Triad Explicit Ratings  
2     Triad Explicit Ratings  
3     Triad Explicit Ratings  
4     Triad Explicit Ratings  
...                      ...  
4025  Triad Explicit Ratings  
4026  Triad Explicit Ratings  
4027  Triad Explicit Ratings  
4028  Triad Explicit Ratings  
4029  Triad Explicit Ratings  

[4030 rows x 7 columns]

In [26]:
triads_ranking_only = df_to_use[df_to_use['ground_truth_type']=='Triad Ranking Order']
triads_ranking_only_corr = ihm.convert_correlation_df_to_a_line_chart_df(triads_ranking_only, empirical_ranking_names=empirical_ranking_triads, column_to_convert='final_ranking_correlate', group_by_methods_array=['cleaned_method_name','exp_with','r_names_used','harmonics_considered','ground_truth_type'])
triads_ranking_only_corr

Normalized values for each rank: [0.2560975609756097, 0.2560975609756097, 0.1280487804878048, 0.5670731707317074, 0.2560975609756097, 0.4512195121951219, 0.4512195121951219, 0.2560975609756097, 0.8719512195121949, 0.1280487804878048, 0.8719512195121949, 1.0, 0.0]
Normalized values for each rank: [0.1150793650793649, 0.1150793650793649, 0.0861678004535148, 0.3633786848072563, 0.1904761904761904, 0.1865079365079363, 0.1865079365079363, 0.1904761904761904, 0.8917233560090703, 0.0861678004535148, 0.8917233560090703, 1.0, 0.0]
Normalized values for each rank: [0.1479729869271598, 0.1479729869271598, 0.0763682614197744, 0.3481540141104351, 0.1886784659548544, 0.2362817785671506, 0.2362817785671506, 0.1886784659548544, 0.8711060817869701, 0.0763682614197744, 0.8711060817869705, 1.0, 0.0]
Normalized values for each rank: [0.2134432237560611, 0.2134432237560609, 0.1024488594617024, 0.4672078320360239, 0.2554659674942698, 0.3853047997744684, 0.3853047997744684, 0.2554659674942696, 0.847538367166

chord_label  normalized_value cleaned_method_name exp_with  \
0             CM          0.256098            Method E   Triads   
1             Cm          0.256098            Method E   Triads   
2          FM2nd          0.128049            Method E   Triads   
3       Fsus42nd          0.567073            Method E   Triads   
4         G#M1st          0.256098            Method E   Triads   
...          ...               ...                 ...      ...   
4025     Adim1st          0.594937            Method A   Triads   
4026       Am1st          0.329114            Method A   Triads   
4027    F#dim2nd          0.594937            Method A   Triads   
4028        Cdim          1.000000            Method A   Triads   
4029        CAug          0.645570            Method A   Triads   

                     r_names_used  harmonics_considered    ground_truth_type  
0         All r_bounds Considered                     2  Triad Ranking Order  
1         All r_bounds Considered                     2  Triad Ranking Order  
2         All r_bounds Considered                     2  Triad Ranking Order  
3         All r_bounds Considered                     2  Triad Ranking Order  
4         All r_bounds Considered                     2  Triad Ranking Order  
...                           ...                   ...                  ...  
4025  Starting from r_lower==0.25                    32  Triad Ranking Order  
4026  Starting from r_lower==0.25                    32  Triad Ranking Order  
4027  Starting from r_lower==0.25                    32  Triad Ranking Order  
4028  Starting from r_lower==0.25                    32  Triad Ranking Order  
4029  Starting from r_lower==0.25                    32  Triad Ranking Order  

[4030 rows x 7 columns]

In [27]:
## joining both dataframes
joined_df = pd.concat([chord_label_df_ranking_intervals, corr_df_ranking_triads, triads_ranking_only_corr], ignore_index=True)
joined_df
joined_df.to_csv('../data_csvs/ihm_combined_intervals_and_triads_corr_values_case.csv', index=False)

In [28]:
joined_df = pd.read_csv('../data_csvs/ihm_combined_intervals_and_triads_corr_values_case.csv')
joined_df

chord_label  normalized_value cleaned_method_name   exp_with  \
0               U          0.000000            Method E  Intervals   
1              8v          0.000000            Method E  Intervals   
2              P5          0.000000            Method E  Intervals   
3              P4          0.000000            Method E  Intervals   
4              M3          0.000000            Method E  Intervals   
...           ...               ...                 ...        ...   
12085     Adim1st          0.594937            Method A     Triads   
12086       Am1st          0.329114            Method A     Triads   
12087    F#dim2nd          0.594937            Method A     Triads   
12088        Cdim          1.000000            Method A     Triads   
12089        CAug          0.645570            Method A     Triads   

                      r_names_used  harmonics_considered  \
0          All r_bounds Considered                     2   
1          All r_bounds Considered                     2   
2          All r_bounds Considered                     2   
3          All r_bounds Considered                     2   
4          All r_bounds Considered                     2   
...                            ...                   ...   
12085  Starting from r_lower==0.25                    32   
12086  Starting from r_lower==0.25                    32   
12087  Starting from r_lower==0.25                    32   
12088  Starting from r_lower==0.25                    32   
12089  Starting from r_lower==0.25                    32   

            ground_truth_type  
0      Interval Ranking Order  
1      Interval Ranking Order  
2      Interval Ranking Order  
3      Interval Ranking Order  
4      Interval Ranking Order  
...                       ...  
12085     Triad Ranking Order  
12086     Triad Ranking Order  
12087     Triad Ranking Order  
12088     Triad Ranking Order  
12089     Triad Ranking Order  

[12090 rows x 7 columns]

In [29]:

for i,r in joined_df.iterrows():
    if r['r_names_used']=='all_ranges':
        joined_df.at[i,'r_names_used']='All r_bounds Considered'
    elif r['r_names_used']=='Starting from r_lower==0.5':
        joined_df.at[i,'r_names_used']='Starting from r_lower==0.25'
joined_df.to_csv('../data_csvs/ihm_combined_intervals_and_triads_corr_values_case.csv', index=False)

In [30]:

harmonics_considered = 13
df_to_consider_corr = joined_df[joined_df['harmonics_considered']==harmonics_considered]
df_to_consider_corr

chord_label  normalized_value cleaned_method_name   exp_with  \
143             U          0.119874            Method E  Intervals   
144            8v          0.000000            Method E  Intervals   
145            P5          0.122761            Method E  Intervals   
146            P4          0.206066            Method E  Intervals   
147            M3          0.337512            Method E  Intervals   
...           ...               ...                 ...        ...   
11838     Adim1st          0.714286            Method A     Triads   
11839       Am1st          0.285714            Method A     Triads   
11840    F#dim2nd          0.714286            Method A     Triads   
11841        Cdim          1.000000            Method A     Triads   
11842        CAug          0.666667            Method A     Triads   

                      r_names_used  harmonics_considered  \
143        All r_bounds Considered                    13   
144        All r_bounds Considered                    13   
145        All r_bounds Considered                    13   
146        All r_bounds Considered                    13   
147        All r_bounds Considered                    13   
...                            ...                   ...   
11838  Starting from r_lower==0.25                    13   
11839  Starting from r_lower==0.25                    13   
11840  Starting from r_lower==0.25                    13   
11841  Starting from r_lower==0.25                    13   
11842  Starting from r_lower==0.25                    13   

            ground_truth_type  
143    Interval Ranking Order  
144    Interval Ranking Order  
145    Interval Ranking Order  
146    Interval Ranking Order  
147    Interval Ranking Order  
...                       ...  
11838     Triad Ranking Order  
11839     Triad Ranking Order  
11840     Triad Ranking Order  
11841     Triad Ranking Order  
11842     Triad Ranking Order  

[390 rows x 7 columns]

In [31]:

ranking_triads = df_to_consider_corr[df_to_consider_corr['exp_with']=='Triads']
ranking_triads


chord_label  normalized_value cleaned_method_name exp_with  \
4173           CM      1.071969e-01            Method E   Triads   
4174           Cm      1.071969e-01            Method E   Triads   
4175        FM2nd      3.307909e-16            Method E   Triads   
4176     Fsus42nd      1.884330e-01            Method E   Triads   
4177       G#M1st      1.255696e-01            Method E   Triads   
...           ...               ...                 ...      ...   
11838     Adim1st      7.142857e-01            Method A   Triads   
11839       Am1st      2.857143e-01            Method A   Triads   
11840    F#dim2nd      7.142857e-01            Method A   Triads   
11841        Cdim      1.000000e+00            Method A   Triads   
11842        CAug      6.666667e-01            Method A   Triads   

                      r_names_used  harmonics_considered  \
4173       All r_bounds Considered                    13   
4174       All r_bounds Considered                    13   
4175       All r_bounds Considered                    13   
4176       All r_bounds Considered                    13   
4177       All r_bounds Considered                    13   
...                            ...                   ...   
11838  Starting from r_lower==0.25                    13   
11839  Starting from r_lower==0.25                    13   
11840  Starting from r_lower==0.25                    13   
11841  Starting from r_lower==0.25                    13   
11842  Starting from r_lower==0.25                    13   

            ground_truth_type  
4173   Triad Explicit Ratings  
4174   Triad Explicit Ratings  
4175   Triad Explicit Ratings  
4176   Triad Explicit Ratings  
4177   Triad Explicit Ratings  
...                       ...  
11838     Triad Ranking Order  
11839     Triad Ranking Order  
11840     Triad Ranking Order  
11841     Triad Ranking Order  
11842     Triad Ranking Order  

[260 rows x 7 columns]

In [32]:
ranking_intervals = df_to_consider_corr[df_to_consider_corr['exp_with']=='Intervals']


# count each row with unique method name
ranking_intervals[ranking_intervals['cleaned_method_name']=='Method E']

chord_label  normalized_value cleaned_method_name   exp_with  \
143            U          0.119874            Method E  Intervals   
144           8v          0.000000            Method E  Intervals   
145           P5          0.122761            Method E  Intervals   
146           P4          0.206066            Method E  Intervals   
147           M3          0.337512            Method E  Intervals   
148           M6          0.372881            Method E  Intervals   
149           m6          0.277499            Method E  Intervals   
150           m3          0.592078            Method E  Intervals   
151           TT          1.000000            Method E  Intervals   
152           m7          0.743204            Method E  Intervals   
153           M2          0.780505            Method E  Intervals   
154           M7          0.675454            Method E  Intervals   
155           m2          0.790963            Method E  Intervals   
1755           U          0.194716            Method E  Intervals   
1756          8v          0.000000            Method E  Intervals   
1757          P5          0.107712            Method E  Intervals   
1758          P4          0.188080            Method E  Intervals   
1759          M3          0.283480            Method E  Intervals   
1760          M6          0.316133            Method E  Intervals   
1761          m6          0.224921            Method E  Intervals   
1762          m3          0.566074            Method E  Intervals   
1763          TT          1.000000            Method E  Intervals   
1764          m7          0.731476            Method E  Intervals   
1765          M2          0.781178            Method E  Intervals   
1766          M7          0.668242            Method E  Intervals   
1767          m2          0.791049            Method E  Intervals   

                     r_names_used  harmonics_considered  \
143       All r_bounds Considered                    13   
144       All r_bounds Considered                    13   
145       All r_bounds Considered                    13   
146       All r_bounds Considered                    13   
147       All r_bounds Considered                    13   
148       All r_bounds Considered                    13   
149       All r_bounds Considered                    13   
150       All r_bounds Considered                    13   
151       All r_bounds Considered                    13   
152       All r_bounds Considered                    13   
153       All r_bounds Considered                    13   
154       All r_bounds Considered                    13   
155       All r_bounds Considered                    13   
1755  Starting from r_lower==0.25                    13   
1756  Starting from r_lower==0.25                    13   
1757  Starting from r_lower==0.25                    13   
1758  Starting from r_lower==0.25                    13   
1759  Starting from r_lower==0.25                    13   
1760  Starting from r_lower==0.25                    13   
1761  Starting from r_lower==0.25                    13   
1762  Starting from r_lower==0.25                    13   
1763  Starting from r_lower==0.25                    13   
1764  Starting from r_lower==0.25                    13   
1765  Starting from r_lower==0.25                    13   
1766  Starting from r_lower==0.25                    13   
1767  Starting from r_lower==0.25                    13   

           ground_truth_type  
143   Interval Ranking Order  
144   Interval Ranking Order  
145   Interval Ranking Order  
146   Interval Ranking Order  
147   Interval Ranking Order  
148   Interval Ranking Order  
149   Interval Ranking Order  
150   Interval Ranking Order  
151   Interval Ranking Order  
152   Interval Ranking Order  
153   Interval Ranking Order  
154   Interval Ranking Order  
155   Interval Ranking Order  
1755  Interval Ranking Order  
1756  Interval Ranking Order  
1757  Interval Ranking Order  
1758  Interval Ranki

In [33]:
empirical_ranking_nums_triads

[1.667,
 2.407,
 2.741,
 2.852,
 2.889,
 3.111,
 3.148,
 3.481,
 3.519,
 3.593,
 3.667,
 3.889,
 5.259]

In [34]:
norm_emp_rankings= [(x - min(empirical_ranking_nums_triads)) / (max(empirical_ranking_nums_triads) - min(empirical_ranking_nums_triads)) for x in empirical_ranking_nums_triads]
norm_emp_rankings

[0.0,
 0.2060133630289532,
 0.29899777282850776,
 0.3298997772828507,
 0.34020044543429834,
 0.4020044543429844,
 0.412305122494432,
 0.5050111358574609,
 0.5155902004454342,
 0.5361915367483295,
 0.5567928730512248,
 0.6185968819599107,
 1.0]

In [35]:
df_gt_triads = pd.DataFrame({
    'normalized_value':norm_emp_rankings,
    'chord_label':empirical_ranking_triads
})
df_gt_triads_ranking_order =  pd.DataFrame({
    'normalized_value':  normalized_values,
    'chord_label':empirical_ranking_triads
})
df_gt_triads_ranking_order


normalized_value chord_label
0           0.000000          CM
1           0.083333          Cm
2           0.166667       FM2nd
3           0.250000    Fsus42nd
4           0.333333      G#M1st
5           0.416667       Csus2
6           0.500000       Csus4
7           0.583333       Fm2nd
8           0.666667     Adim1st
9           0.750000       Am1st
10          0.833333    F#dim2nd
11          0.916667        Cdim
12          1.000000        CAug

In [36]:
ranking_triads

chord_label  normalized_value cleaned_method_name exp_with  \
4173           CM      1.071969e-01            Method E   Triads   
4174           Cm      1.071969e-01            Method E   Triads   
4175        FM2nd      3.307909e-16            Method E   Triads   
4176     Fsus42nd      1.884330e-01            Method E   Triads   
4177       G#M1st      1.255696e-01            Method E   Triads   
...           ...               ...                 ...      ...   
11838     Adim1st      7.142857e-01            Method A   Triads   
11839       Am1st      2.857143e-01            Method A   Triads   
11840    F#dim2nd      7.142857e-01            Method A   Triads   
11841        Cdim      1.000000e+00            Method A   Triads   
11842        CAug      6.666667e-01            Method A   Triads   

                      r_names_used  harmonics_considered  \
4173       All r_bounds Considered                    13   
4174       All r_bounds Considered                    13   
4175       All r_bounds Considered                    13   
4176       All r_bounds Considered                    13   
4177       All r_bounds Considered                    13   
...                            ...                   ...   
11838  Starting from r_lower==0.25                    13   
11839  Starting from r_lower==0.25                    13   
11840  Starting from r_lower==0.25                    13   
11841  Starting from r_lower==0.25                    13   
11842  Starting from r_lower==0.25                    13   

            ground_truth_type  
4173   Triad Explicit Ratings  
4174   Triad Explicit Ratings  
4175   Triad Explicit Ratings  
4176   Triad Explicit Ratings  
4177   Triad Explicit Ratings  
...                       ...  
11838     Triad Ranking Order  
11839     Triad Ranking Order  
11840     Triad Ranking Order  
11841     Triad Ranking Order  
11842     Triad Ranking Order  

[260 rows x 7 columns]

In [37]:
width=175
height=175



In [38]:

base_chart  = alt.Chart().mark_line().encode(
    x=alt.X('chord_label',sort=empirical_ranking_intervals),
    y=alt.Y('normalized_value'),
    color=alt.Color('cleaned_method_name:N',title='Different Methods')
)

ground_truth_line = alt.Chart(df_gt).mark_line(color='black',strokeDash=[5,5]).encode(
    x=alt.X('chord_label', title="Intervals labels ranked",sort=empirical_ranking_intervals),
    y=alt.Y('normalized_value', title=None)
)

facet_gt_intervals = (base_chart + ground_truth_line).properties(width=width,height=height).facet(data=ranking_intervals,row=alt.Row('r_names_used:N',title='Normalized Correlation Score using different r_bounds',),title=alt.Title('Intervals Ranking Order',anchor='middle',fontSize=12,fontWeight='normal'))
facet_gt_intervals


alt.FacetChart(...)

In [39]:
triads_chart = alt.Chart().mark_line().encode(
    x=alt.X('chord_label', sort=empirical_ranking_triads),
    y=alt.Y('normalized_value', title=None),
    color=alt.Color('cleaned_method_name:N')
)
layered_triads_chart_emp = (triads_chart + alt.Chart(df_gt_triads).mark_line(color='black',strokeDash=[5,5]).encode(
    x=alt.X('chord_label', title="Triad labels ranked",sort=empirical_ranking_triads),
    y=alt.Y('normalized_value', title=None)
)).properties(width=width,height=height).facet(data=ranking_triads,row=alt.Row('r_names_used:N',header=None),title=alt.Title('Triads with Explicit Ratings',anchor='middle',fontSize=12,fontWeight='normal'))

layered_triads_chart_rank = (triads_chart + alt.Chart(df_gt_triads_ranking_order).mark_line(color='black',strokeDash=[5,5]).encode(
    x=alt.X('chord_label', title="Triad labels ranked",sort=empirical_ranking_triads),
    y=alt.Y('normalized_value', title=None)
)).properties(width=width,height=height).facet(
    data=ranking_triads,row=alt.Row(
        'r_names_used:N',header=None
        ),title=alt.Title(
            'Triads with Explicit Ratings',anchor='middle',fontSize=12,fontWeight='normal'
        )
    )


layered_triads_chart_emp

(facet_gt_intervals | (layered_triads_chart_rank | layered_triads_chart_emp)).resolve_scale(y='shared').properties(
    title="Normalized tension score for each Chord Label compared to Empirical Rankings considering 13 harmonics"
        ).configure_title(
            anchor='middle'
        ).configure_header(
            titleAnchor='middle',
            
        ).configure_legend(
            orient='bottom',titleAnchor='middle',titleAlign='center'
        )


alt.HConcatChart(...)

In [40]:
joined_df

chord_label  normalized_value cleaned_method_name   exp_with  \
0               U          0.000000            Method E  Intervals   
1              8v          0.000000            Method E  Intervals   
2              P5          0.000000            Method E  Intervals   
3              P4          0.000000            Method E  Intervals   
4              M3          0.000000            Method E  Intervals   
...           ...               ...                 ...        ...   
12085     Adim1st          0.594937            Method A     Triads   
12086       Am1st          0.329114            Method A     Triads   
12087    F#dim2nd          0.594937            Method A     Triads   
12088        Cdim          1.000000            Method A     Triads   
12089        CAug          0.645570            Method A     Triads   

                      r_names_used  harmonics_considered  \
0          All r_bounds Considered                     2   
1          All r_bounds Considered                     2   
2          All r_bounds Considered                     2   
3          All r_bounds Considered                     2   
4          All r_bounds Considered                     2   
...                            ...                   ...   
12085  Starting from r_lower==0.25                    32   
12086  Starting from r_lower==0.25                    32   
12087  Starting from r_lower==0.25                    32   
12088  Starting from r_lower==0.25                    32   
12089  Starting from r_lower==0.25                    32   

            ground_truth_type  
0      Interval Ranking Order  
1      Interval Ranking Order  
2      Interval Ranking Order  
3      Interval Ranking Order  
4      Interval Ranking Order  
...                       ...  
12085     Triad Ranking Order  
12086     Triad Ranking Order  
12087     Triad Ranking Order  
12088     Triad Ranking Order  
12089     Triad Ranking Order  

[12090 rows x 7 columns]

## Corr chart facet

In [59]:
df['r_names_used'].unique()

array(['All r_bounds Considered', 'Starting from r_lower==0.25'],
      dtype=object)

In [64]:
df_harm = df[df['harmonics_considered']<=18]

df_harm = df_harm[df_harm['distributive']!='False']

df_harm.distributive.unique()
df_harm1 = df_harm[df_harm['distributive']!='all_modulations_weight']

df_harm2 = df_harm[df_harm['distributive']!='True']

In [65]:


corr_cart = alt.Chart(df_harm1).mark_rect(align='center',stroke='black',strokeWidth=0.5).encode(
    x=alt.X('harmonics_considered:O',scale=alt.Scale(clamp=True),axis=alt.Axis(title='Harmonics Considered',labelAngle=0)),
    y=alt.Y('cleaned_method_name:O'),
    color=alt.Color('correlation:Q',scale=alt.Scale(domain=[-0.2, 1], scheme='viridis'),
                    legend=alt.Legend(title='Correlation Coefficient')),
)

predicate = alt.datum.correlation >= 0.5
text_chart = alt.Chart(df_harm1).mark_text( align='center').encode(
    x=alt.X('harmonics_considered:O',scale=alt.Scale(clamp=True)),
    y=alt.Y('cleaned_method_name:O',title=None),
    text=alt.Text('correlation:Q',format='.3f'),
    color=alt.condition(predicate, alt.value('black'), alt.value('white'))
)
(corr_cart + text_chart).properties(width=575, height=100).facet(
    row=alt.Row(   'ground_truth_type:N',title='Ground Truth Type'),
    column=alt.Column('r_names_used:N',title='Different r_bounds considered')
    ).properties(
        title='Heatmap of Correlation Values For Different Harmonics Considered'
    ).configure_title(anchor='middle').configure_legend(orient='bottom',titleOrient='left')


alt.FacetChart(...)

In [66]:


corr_cart = alt.Chart(df_harm2).mark_rect(align='center',stroke='black',strokeWidth=0.5).encode(
    x=alt.X('harmonics_considered:O',scale=alt.Scale(clamp=True),axis=alt.Axis(title='Harmonics Considered',labelAngle=0)),
    y=alt.Y('cleaned_method_name:O'),
    color=alt.Color('correlation:Q',scale=alt.Scale(domain=[-0.2, 1], scheme='viridis'),
                    legend=alt.Legend(title='Correlation Coefficient')),
)

predicate = alt.datum.correlation >= 0.5
text_chart = alt.Chart(df_harm2).mark_text( align='center').encode(
    x=alt.X('harmonics_considered:O',scale=alt.Scale(clamp=True)),
    y=alt.Y('cleaned_method_name:O',title=None),
    text=alt.Text('correlation:Q',format='.3f'),
    color=alt.condition(predicate, alt.value('black'), alt.value('white'))
    
)
(corr_cart + text_chart).properties(width=575, height=100).facet(
    row=alt.Row(   'ground_truth_type:N',title='Ground Truth Type'),
    column=alt.Column('r_names_used:N',title='Different r_bounds considered')
    ).properties(
        title='Heatmap of Correlation Values For Different Harmonics Considered'
    ).configure_title(anchor='middle').configure_legend(orient='bottom',titleOrient='left')


alt.FacetChart(...)